# Instructions

* This notebook is refered to MScFE 690 Capstone - Module 6 - Develope and it is finished and running succefully, for an ongoing updated code go to the vLive version.
* Since the notebook requires the instalation of modules it is required to restart the sessions afer the modules are installed.


In [ ]:
import requests
import pandas as pd
import os
import time
from datetime import date, datetime, timedelta
import json
import re
import yfinance as yf

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.colors as pc
import plotly.graph_objects as go
import matplotlib.dates as mdates
from scipy.optimize import minimize
from plotly.subplots import make_subplots

from plotly.subplots import make_subplots
import os
import requests
import numpy as np

try:
  import quiverquant
except:
  !pip install quiverquant
  import quiverquant

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


In [ ]:
# Create output directory
os.makedirs("data", exist_ok=True)

# Data collection

## Configuration

In [ ]:
POLYGON_KEY = "ft2rquZoprD0MSBmJqQfD_8qNsxrkK_1"
QUIVER_TOKEN = "a8dcf66a9fd588b78513ccedb4b92acc948ac6e3"

In [ ]:
# Get the directory of this script
SCRIPT_DIR = os.getcwd()
# Congressional term date ranges
CONGRESS_START_DATE = "2019-01-03"  # 116th Congress start
CONGRESS_END_DATE = "2025-01-02"    # 118th Congress end

# Major economic states for geographic filtering
MAJOR_STATES = ['CA', 'NY', 'TX', 'FL', 'IL', 'PA', 'OH', 'GA', 'NC', 'MI',
                'NJ', 'VA', 'WA', 'AZ', 'MA', 'TN', 'CO', 'MD', 'CT', 'AL']

# Output directory
OUTPUT_DIR = os.path.join(SCRIPT_DIR, 'output')
os.makedirs(OUTPUT_DIR, exist_ok=True)

In [ ]:
lawmakers = [
    # --- Senators ---
    # {"name": "Ron Wyden", "party": "Democratic", "chamber": "Senate", "state": "OR", "bioguide": "W000779"},
    # {"name": "Thomas R. Carper", "party": "Democratic", "chamber": "Senate", "state": "DE", "bioguide": "C000174"},
    # {"name": "A. Mitchell Jr. McConnell", "party": "Republican", "chamber": "Senate", "state": "KY", "bioguide": "M000355"},

    # # --- House of Representatives ---

    {"name": "Josh Gottheimer", "party": "Democratic", "chamber": "House", "state": "NJ", "bioguide": "G000583"},
    {"name": "Nancy Pelosi", "party": "Democratic", "chamber": "House", "state": "CA", "bioguide": "P000197"},
    {"name": "Kevin Hern", "party": "Republican", "chamber": "House", "state": "OK", "bioguide": "H001082"},
    {"name": "Mark Green", "party": "Republican", "chamber": "House", "state": "TN", "bioguide": "G000590"},
    {"name": "Bradley S. Schneider", "party": "Democratic", "chamber": "House", "state": "IL", "bioguide": "S001190"},
    {"name": "Virginia Foxx", "party": "Republican", "chamber": "House", "state": "NC", "bioguide": "F000450"},
    {"name": "Kim Schrier", "party": "Democratic", "chamber": "House", "state": "WA", "bioguide": "S001216"},
    {"name": "Mikie Sherrill", "party": "Democratic", "chamber": "House", "state": "NJ", "bioguide": "S001207"},
    {"name": "Daniel Meuser", "party": "Republican", "chamber": "House", "state": "PA", "bioguide": "M001204"},
    {"name": "Susie Lee", "party": "Democratic", "chamber": "House", "state": "NV", "bioguide": "L000590"},
    {"name": "John W. Rose", "party": "Republican", "chamber": "House", "state": "TN", "bioguide": "R000612"},
    {"name": "Brian Mast", "party": "Republican", "chamber": "House", "state": "FL", "bioguide": "M001199"},
    {"name": "Carol Devine Miller", "party": "Republican", "chamber": "House", "state": "WV", "bioguide": "M001205"},
    {"name": "Michael C. Burgess", "party": "Republican", "chamber": "House", "state": "TX", "bioguide": "B001248"},
    {"name": "Pete Sessions", "party": "Republican", "chamber": "House", "state": "TX", "bioguide": "S000250"},
    {"name": "Lois Frankel", "party": "Democratic", "chamber": "House", "state": "FL", "bioguide": "F000462"},
    {"name": "Earl Blumenauer", "party": "Democratic", "chamber": "House", "state": "OR", "bioguide": "B000574"},
    {"name": "Michael Garcia", "party": "Republican", "chamber": "House", "state": "CA", "bioguide": "G000061"},
    {"name": "Donald Sternoff Beyer Jr", "party": "Democratic", "chamber": "House", "state": "VI", "bioguide": "B001292"},
    {"name": "Debbie Dingell", "party": "Democratic", "chamber": "House", "state": "MI", "bioguide": "D000624"},

]
lawmakers = pd.DataFrame(lawmakers)
lawmakers.to_csv("data/lawmakers.csv", index=False)



## Yfinance data

In [ ]:
# 1. Fetch Data
ticker = "NVDA"
df = yf.download(ticker, period="1y", interval="1d")
df = df.stack(level='Ticker').reset_index()

# 2. Create Subplots (2 Rows: Price on top, Volume on bottom)
# row_heights=[0.7, 0.3] gives 70% space to Price, 30% to Volume
fig = make_subplots(
    rows=2, cols=1,
    shared_xaxes=True,
    vertical_spacing=0.03,
    subplot_titles=(f'{ticker} Price', 'Volume'),
    row_heights=[0.7, 0.3]
)

# 3. Add Candlestick Trace (Row 1)
fig.add_trace(go.Candlestick(
    x=df.Date,
    open=df['Open'],
    high=df['High'],
    low=df['Low'],
    close=df['Close'],
    name='Price'
), row=1, col=1)

# 4. Add Volume Trace (Row 2)
# We color the volume bars based on price change (Green for up, Red for down)
colors = ['green' if row['Open'] - row['Close'] >= 0
          else 'red' for index, row in df.iterrows()]

fig.add_trace(go.Bar(
    x=df.Date,
    y=df['Volume'],
    marker_color=colors,
    name='Volume'
), row=2, col=1)

# 5. Add Moving Average (Optional, on Row 1)
df['MA20'] = df['Close'].rolling(window=20).mean()
fig.add_trace(go.Scatter(
    x=df.Date,
    y=df['MA20'],
    line=dict(color='orange', width=2),
    name='20-Day MA'
), row=1, col=1)

# 6. Final Layout Adjustments
fig.update_layout(
    title=f'{ticker} Candlestick Chart with Volume',
    template='plotly_dark',
    xaxis_rangeslider_visible=False, # Hides the slider (redundant with zoom)
    height=800 # Taller figure to accommodate both plots
)

# Show the Plot
fig.show()

[*********************100%***********************]  1 of 1 completed


In [ ]:
df = yf.download(ticker, period="1y", interval="1d", ignore_tz=True)

[*********************100%***********************]  1 of 1 completed


In [ ]:
clean_df = df.stack(level='Ticker').reset_index()
clean_df.head()

Price       Date Ticker       Close        High         Low        Open  \
0     2025-02-10   NVDA  133.533478  134.963079  129.924464  130.054419   
1     2025-02-11   NVDA  132.763702  134.443236  130.984190  132.543761   
2     2025-02-12   NVDA  131.104141  132.203847  129.044707  129.984452   
3     2025-02-13   NVDA  135.253006  136.462682  131.134137  131.524030   
4     2025-02-14   NVDA  138.812042  139.211927  135.462952  136.442680   

Price     Volume  
0      216989100  
1      178902400  
2      160278600  
3      197430000  
4      195479600

## Quiver transaction history

In [ ]:
class CustomQuiver(quiverquant.quiver):

    def congress_trading(self, ticker="", politician=True, recent=False, representative="", bioguide=""):


      if recent:
          urlStart = 'https://api.quiverquant.com/beta/live/congresstrading'
      else:
          urlStart = 'https://api.quiverquant.com/beta/bulk/congresstrading'

      if politician:
          representative = representative.replace(" ", "%20")
          ticker = ticker.replace(" ", "%20")

          if representative:
            url = urlStart+"?representative="+representative+ticker

          elif bioguide:
            url = urlStart+"?bioguide_id="+bioguide+ticker


      elif len(ticker)>0:
          url = urlStart+"/"+ticker
      else:
          url = urlStart
      print(url)
      r = requests.get(url, headers=self.headers)
      j = json.loads(r.content)
      df = pd.DataFrame(j)
      return df

# === API KEYS  ===
# - Quiver Quantitative: https://www.quiverquant.com/ (paid subscription required for API access, but has free trial)
# - Documentation on https://api.quiverquant.com/docs/#/ and https://github.com/Quiver-Quantitative/python-api

QUIVER_TOKEN = "a8dcf66a9fd588b78513ccedb4b92acc948ac6e3"

# # 1 Initialize Quiver client (token required for full access)

# qq = quiverquant.quiver(QUIVER_TOKEN)

quiver = CustomQuiver(QUIVER_TOKEN)


In [ ]:
def fetch_congress_trading(use_cache=True, cache_file=None):
    """
    Fetch all congress trading data from Quiver API.

    Parameters:
    -----------
    use_cache : bool
        If True, use cached data if available
    cache_file : str
        Path to cache file

    Returns:
    --------
    pd.DataFrame : All congress trading records
    """
    if cache_file is None:
        cache_file = os.path.join(OUTPUT_DIR, 'raw_congress_trades.csv')

    # Check cache
    if use_cache and os.path.exists(cache_file):
        print(f"Loading cached data from {cache_file}")
        df = pd.read_csv(cache_file)
        return df

    # Fetch from API
    print("Fetching congress trading data from Quiver API...")
    quiver = CustomQuiver(QUIVER_TOKEN)
    df = quiver.congress_trading(recent=False, politician=False)

    # Save cache
    df.to_csv(cache_file, index=False)
    print(f"Saved {len(df)} records to {cache_file}")

    return df

In [ ]:
raw_df = fetch_congress_trading(use_cache=True)

Fetching congress trading data from Quiver API...
https://api.quiverquant.com/beta/bulk/congresstrading
Saved 109163 records to /content/output/raw_congress_trades.csv


In [ ]:
def filter_by_date_range(df, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """
    Filter trading data to specified date range.

    Parameters:
    -----------
    df : pd.DataFrame
        Trading data
    start_date : str
        Start date (YYYY-MM-DD)
    end_date : str
        End date (YYYY-MM-DD)

    Returns:
    --------
    pd.DataFrame : Filtered data
    """
    df_filtered = df.loc[
        (df['Traded'] >= start_date) &
        (df['Traded'] <= end_date)
    ].copy()

    print(f"Filtered to {len(df_filtered)} records between {start_date} and {end_date}")
    return df_filtered


In [ ]:
def clean_trading_data(df):
    """
    Clean and preprocess trading data.

    Parameters:
    -----------
    df : pd.DataFrame
        Raw trading data

    Returns:
    --------
    pd.DataFrame : Cleaned data
    """
    df = df.copy()

    # Convert numeric columns
    df['Trade_Size_USD'] = pd.to_numeric(df['Trade_Size_USD'], errors='coerce')
    df['excess_return'] = pd.to_numeric(df['excess_return'], errors='coerce')

    # Drop rows with missing critical values
    df = df.dropna(subset=['Trade_Size_USD', 'excess_return'])

    # Filter out non-positive trade sizes
    df = df[df['Trade_Size_USD'] > 0]

    # Convert dates
    df['Traded'] = pd.to_datetime(df['Traded'])
    df['Filed'] = pd.to_datetime(df['Filed'], errors='coerce')

    # Extract state from District (e.g., 'CA11' -> 'CA')
    df['State'] = df['District'].astype(str).str.strip().str.extract(r'([A-Z]{2})', expand=False)

    # Add year column for yearly analysis
    df['Year'] = df['Traded'].dt.year

    print(f"Cleaned data: {len(df)} records, {df['Name'].nunique()} unique politicians")
    return df



In [ ]:
df_date_filtered = filter_by_date_range(raw_df)

Filtered to 56932 records between 2019-01-03 and 2025-01-02


In [ ]:
cleaned_df = clean_trading_data(df_date_filtered)

Cleaned data: 52705 records, 244 unique politicians


# EDA

In [ ]:
class Congressman:
  def __init__(self, name:str, party:str, chamber:str, state:str, bioguide:str, quiverClient):

    self.name = name
    self.party = party
    self.chamber = chamber
    self.state = state
    self.bioguide = bioguide
# -------------

    self.transactions = self.get_transactions(quiverClient)
    self.tickers = self.get_tickers()

    self.positions = self.get_positions()
    self.positions45days = self.get_positions(delay=True)

    self.portfolio = None
    self.portfolio45days = None

    self.weights = None
    self.weights45days = None

    self.returns = None
    self.returns45days = None

  def get_transactions(self, quiverClient):

    transactions = quiverClient.congress_trading(bioguide=self.bioguide)
    if transactions.empty:
        print("No transacction history for ", self.name)
        return None

    transactions = transactions[~transactions['TickerType'].str.contains('OP|None', na=True)]
    transactions = transactions[['Ticker', 'TickerType', 'Traded', 'Transaction', 'Description', 'Filed', 'Trade_Size_USD']]

    # Removing options trades
    transactions = transactions[~transactions['Description'].str.contains('options', na=False, case=False)]

    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'].str.extract(r'(\d{1,3}(?:,\d{3})*)', expand=False)

    # Remove commas from the extracted strings and convert to a numeric type (float)
    # Errors='coerce' will turn values that can't be converted into NaN
    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'].str.replace(',', '', regex=False).astype(float)

    transactions['Transaction'] = transactions['Transaction'].map({"Purchase": 1, "Sale": -1})
    transactions['Transaction'].dropna

    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'] * transactions['Transaction']

    transactions["Traded"] = pd.to_datetime(transactions["Traded"])
    transactions = transactions.set_index('Traded')

    return transactions

  def get_tickers(self):

    tickers = self.transactions['Ticker'].unique().tolist()

    # Mapping for known ticker changes (keep this)
    ticker_mapping = {'FB': 'META'}  # add more if needed
    tickers = [ticker_mapping.get(t, t) for t in tickers]

    # Strict filter: only allow typical US stock ticker patterns
    # - Uppercase letters, numbers, and dots (for class shares like BRK.B)
    # - No spaces, no commas, no lowercase, reasonable length
    def is_valid_ticker(t):
        return (
            bool(re.fullmatch(r'[A-Z0-9\.]{1,10}', t)) and
            ' ' not in t and
            ',' not in t and
            t.isupper()
        )

    valid_tickers = [t for t in tickers if is_valid_ticker(t)]

    manual_excludes = {'BFET', 'WORK', 'VSNT'}
    valid_tickers = [t for t in valid_tickers if t not in manual_excludes]

    print(valid_tickers)
    return valid_tickers

  def get_positions(self, delay=False):

    if self.transactions.empty:
      # Fallback empty DataFrame
      print('No positions for: ', self.name)
      return pd.DataFrame(columns=self.tickers)

    trans = self.transactions.copy()

    # Apply 45-day delay if requested
    trade_date_col = "Traded"  # default uses original index

    if delay:
        print(f"Delayed for: {self.name}")
        trans['TradedDelay45'] = trans.index + pd.Timedelta(days=45)
        trade_date_col = "TradedDelay45"

    # Daily net dollar flows by ticker
    daily_delta = trans.pivot_table(
        index=trade_date_col,
        columns="Ticker",
        values="Trade_Size_USD",
        aggfunc="sum"
    ).sort_index()

    print(f"Daily delta for {self.name}:")
    positions = daily_delta.cumsum()

    full_index = pd.date_range(
        start=positions.index.min(),
        end=positions.index.max(),
        freq="D"
    )

    # Reindex to daily, forward-fill holdings, zero before first trade
    positions = (
        positions
        .reindex(full_index)
        .ffill()
        .fillna(0)
    )

    start_date_str = '2019-01-03'
    end_date_str = '2025-01-03'
    start = date.fromisoformat(start_date_str)
    end = date.fromisoformat(end_date_str)

    # Final safety: only our tickers, sorted columns
    target_index = pd.date_range(start=start, end=end, freq='D')
    positions = positions.reindex(target_index)

    positions = positions.loc[:, positions.columns.isin(self.tickers)]

    return positions

# -----

lawmakers_test = [
    # --- Senators ---
    {"name": "Mitch McConnell", "party": "Republican", "chamber": "Senate", "state": "KY", "bioguide": "M000355"},
    {"name": "Nancy Pelosi", "party": "Democrat", "chamber": "House", "state": "CA", "bioguide": "P000197"},
    {"name": "Ted Cruz", "party": "Republican", "chamber": "Senate", "state": "TX", "bioguide": "C001098"},  # state fixed from "ME"
  ]

congressmen = []

for l in lawmakers_test:
    congressman = Congressman(
        name=l["name"],
        party=l["party"],
        chamber=l["chamber"],
        state=l["state"],
        bioguide=l["bioguide"],
        quiverClient=quiver
    )
    congressmen.append(congressman)



all_tickers = [ticker for c in congressmen for ticker in c.tickers]
unique_tickers = list(set(all_tickers))  # removes duplicates
unique_tickers.sort()                    # optional: alphabetical order


def get_prices(tickers):
  start_date_str = '2019-01-03'
  end_date_str = '2025-01-03'
  start_date = date.fromisoformat(start_date_str)
  end_date = date.fromisoformat(end_date_str)

  all_ticker_prices = {}

  if tickers:
      print(f"Downloading prices for {len(tickers)} tickers...")
      prices_multi = yf.download(
          tickers,
          start=start_date_str,
          end=end_date_str,
          interval='1d',
          auto_adjust=True,
          progress=True
      )

      # prices_multi['Close'] is a DataFrame with columns = tickers
      close_df = prices_multi['Close']

      for ticker in tickers:
          series = close_df[ticker]
          if series.notna().any():  # has at least some real data
              all_ticker_prices[ticker] = series
          else:
              print(f"No valid price data for {ticker}")

  else:
      print("No valid tickers found.")

  # Create a master DataFrame with a full date range
  full_date_range = pd.date_range(start=start_date_str, end=end_date_str, freq='D')
  prices_df = pd.DataFrame(index=full_date_range)

  # Populate the master DataFrame with ticker prices
  for ticker, prices_series in all_ticker_prices.items():
      prices_df[ticker] = prices_series

  prices_df = prices_df.dropna(how='all')
  prices_df = prices_df.fillna(0)

  return prices_df

prices = get_prices(unique_tickers)
print(prices)


https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=M000355
['LAZR', 'WFC', 'KR', 'IR', 'VMC']
Daily delta for Mitch McConnell:
Delayed for: Mitch McConnell
Daily delta for Mitch McConnell:
https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=P000197
['AB', 'AAPL', 'GOOGL', 'DIS', 'PYPL', 'AMZN', 'NVDA', 'MSFT', 'V', 'TSLA', 'NFLX', 'RBLX', 'WBD', 'CRWD', 'META', 'MORN', 'IBKR', 'T']
Daily delta for Nancy Pelosi:
Delayed for: Nancy Pelosi
Daily delta for Nancy Pelosi:
https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=C001098
['GS', 'BTC', 'PAGP', 'OKE']
Daily delta for Ted Cruz:
Delayed for: Ted Cruz
Daily delta for Ted Cruz:


[*********************100%***********************]  27 of 27 completed

                  AAPL         AB        AMZN        BTC        CRWD  \
2019-01-03   33.799675  15.191702   75.014000   0.000000    0.000000   
2019-01-04   35.242554  15.540111   78.769501   0.000000    0.000000   
2019-01-07   35.164108  15.462686   81.475502   0.000000    0.000000   
2019-01-08   35.834454  15.540111   82.829002   0.000000    0.000000   
2019-01-09   36.442982  15.517986   82.971001   0.000000    0.000000   
...                ...        ...         ...        ...         ...   
2024-12-26  257.853760  34.239239  227.050003  42.330002  365.079987   
2024-12-27  254.439224  34.083649  223.750000  41.820000  354.989990   
2024-12-30  251.064484  33.369759  221.300003  41.750000  349.309998   
2024-12-31  249.292511  33.946362  219.389999  41.869999  342.160004   
2025-01-02  242.752090  33.918907  220.220001  43.160000  347.339996   

                   DIS       GOOGL          GS       IBKR         IR  ...  \
2019-01-03  102.629349   50.889000  144.015778  12.552105 

# Analysis

In [ ]:
INITIAL_CAPITAL = 100000  # For normalization

# Data file paths
RAW_TRADES_PATH = './output/raw_congress_trades.csv'
LAWMAKERS_PATH = './data/lawmakers.csv'

# Snapshot dates for pie charts
SNAPSHOT_DATES = [
    '2019-01-03',  # Start
    '2019-12-31',  # Year-end 2019
    '2020-12-31',  # Year-end 2020
    '2021-12-31',  # Year-end 2021
    '2022-12-31',  # Year-end 2022
    '2023-12-31',  # Year-end 2023
    '2024-12-31',  # Year-end 2024
    '2025-01-02',  # End
]


In [ ]:
cleaned_df.columns

Index(['Ticker', 'TickerType', 'Company', 'Traded', 'Transaction',
       'Trade_Size_USD', 'Status', 'Subholding', 'Description', 'Name',
       'BioGuideID', 'Filed', 'Party', 'District', 'Chamber', 'Comments',
       'Quiver_Upload_Time', 'excess_return', 'State', 'last_modified',
       'Year'],
      dtype='object')

In [ ]:
class Congressman_df:
    """Represents a legislator with their trading history and positions.

    Uses pre-loaded DataFrame instead of API calls.
    """

    def __init__(self, name: str, party: str, chamber: str, state: str,
                 bioguide: str, trades_df: pd.DataFrame):
        self.name = name
        self.party = party
        self.chamber = chamber
        self.state = state
        self.bioguide = bioguide

        self.transactions = self._get_transactions(trades_df)
        self.tickers = self._get_tickers() if self.transactions is not None else []
        self.positions_df = self._build_positions_df() if self.transactions is not None else pd.DataFrame()

    def _get_transactions(self, trades_df: pd.DataFrame):
        """Filter and clean transaction history from DataFrame."""
        try:
            # Filter by BioGuideID
            transactions = trades_df[trades_df['BioGuideID'] == self.bioguide].copy()

            if transactions.empty:
                # Try by name as fallback
                transactions = trades_df[trades_df['Name'] == self.name].copy()

            if transactions.empty:
                print(f"No transactions found for {self.name}")
                return None

            # Filter out options and non-stock trades
            if 'TickerType' in transactions.columns:
                transactions = transactions[~transactions['TickerType'].str.contains('OP|None', na=True)]

            # Keep relevant columns
            keep_cols = ['Ticker', 'TickerType', 'Traded', 'Transaction',
                         'Description', 'Filed', 'Trade_Size_USD']
            available_cols = [c for c in keep_cols if c in transactions.columns]
            transactions = transactions[available_cols].copy()

            # Filter out options from description
            if 'Description' in transactions.columns:
                transactions = transactions[~transactions['Description'].str.contains('options', na=False, case=False)]

            # Parse trade size - handle both string and numeric values
            transactions['Trade_Size_USD'] = pd.to_numeric(transactions['Trade_Size_USD'], errors='coerce')

            # Convert dates
            transactions['Traded'] = pd.to_datetime(transactions['Traded'])
            transactions['Filed'] = pd.to_datetime(transactions['Filed'])

            # Drop rows with missing trade size
            # transactions = transactions.dropna(subset=['Trade_Size_USD'])

            return transactions.sort_values('Traded').reset_index(drop=True)

        except Exception as e:
            print(f"Error processing transactions for {self.name}: {e}")
            return None

    def _get_tickers(self):
        """Extract unique valid stock tickers."""
        if self.transactions is None:
            return []

        tickers = self.transactions['Ticker'].unique().tolist()

        # Mapping for known ticker changes
        ticker_mapping = {'FB': 'META'}
        tickers = [ticker_mapping.get(t, t) for t in tickers]

        # Validate ticker format
        def is_valid_ticker(t):
            return (
                bool(re.fullmatch(r'[A-Z0-9\.]{1,10}', str(t))) and
                ' ' not in str(t) and
                ',' not in str(t) and
                str(t).isupper()
            )

        valid_tickers = [t for t in tickers if is_valid_ticker(t)]
        return valid_tickers

    def _build_positions_df(self):
        """Build cumulative positions DataFrame."""
        if self.transactions is None or self.transactions.empty:
            return pd.DataFrame()

        records = []
        for _, tx in self.transactions.iterrows():
            ticker = tx['Ticker']
            traded_date = tx['Traded']
            amount = tx['Trade_Size_USD']

            # Determine direction
            if tx['Transaction'] in ['Purchase', 'Buy']:
                sign = 1
            elif tx['Transaction'] in ['Sale', 'Sell', 'Sale (Full)', 'Sale (Partial)']:
                sign = -1
            else:
                continue

            records.append({
                'Date': traded_date,
                'Ticker': ticker,
                'Amount': sign * amount,
                'Filed': tx['Filed'],
                'Trade_Size_USD': amount
            })

        if not records:
            return pd.DataFrame()

        return pd.DataFrame(records).sort_values('Date').reset_index(drop=True)

    def get_position(self, as_of_date, date_type='Date'):
        """Get portfolio positions as of a specific date (in dollar amounts)."""
        if self.positions_df.empty:
            return {}

        as_of = pd.to_datetime(as_of_date)
        df = self.positions_df[self.positions_df[date_type] <= as_of]

        if df.empty:
            return {}

        positions = df.groupby('Ticker')['Amount'].sum().to_dict()
        # Only keep positive positions
        return {k: v for k, v in positions.items() if v > 0}


    def get_portfolio_composition(self, as_of_date, prices_df):
        """Get detailed portfolio composition with current market values.

        Args:
            as_of_date: Date to get composition for
            prices_df: DataFrame of prices from fetch_prices()

        Returns:
            DataFrame with columns: Ticker, Shares, Price, Value, Weight
        """
        as_of = pd.to_datetime(as_of_date)

        # Get cumulative positions in dollars
        dollar_positions = self.get_position(as_of)

        if not dollar_positions:
            print(f"No positions found for {self.name} as of {as_of_date}")
            return pd.DataFrame()

        records = []
        for ticker, dollar_amount in dollar_positions.items():
            # Get price on the as_of date
            price = get_price_on_date(prices_df, ticker, as_of)

            if price and price > 0:
                shares = dollar_amount / price
                current_value = shares * price
                records.append({
                    'Ticker': ticker,
                    'Cost_Basis_USD': dollar_amount,
                    'Shares': shares,
                    'Price': price,
                    'Value': current_value
                })

        if not records:
            return pd.DataFrame()

        df = pd.DataFrame(records)
        total_value = df['Value'].sum()
        df['Weight'] = (df['Value'] / total_value * 100).round(2)
        df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Add summary info
        print(f"\n{'='*60}")
        print(f"Portfolio Composition for {self.name}")
        print(f"As of: {as_of_date}")
        print(f"{'='*60}")
        print(f"Total Value: ${total_value:,.2f}")
        print(f"Number of Positions: {len(df)}")
        print(f"{'='*60}\n")

        return df




In [ ]:
def fetch_prices(tickers: list, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """Fetch historical prices for all tickers."""
    print(f"Fetching prices for {len(tickers)} tickers...")

    # Add buffer for date lookups
    start_dt = pd.to_datetime(start_date) - timedelta(days=30)
    end_dt = pd.to_datetime(end_date) + timedelta(days=5)

    all_prices = {}
    failed_tickers = []

    for i, ticker in enumerate(tickers):
        try:
            data = yf.download(ticker, start=start_dt, end=end_dt, progress=False)
            if not data.empty:
                # Handle potential multi-level columns from yfinance
                close_col = data['Close']
                if isinstance(close_col, pd.DataFrame):
                    # Multi-level columns - flatten
                    close_col = close_col.iloc[:, 0]
                # Ensure we have a Series with float values
                all_prices[ticker] = close_col.astype(float)
            else:
                failed_tickers.append(ticker)
        except Exception as e:
            failed_tickers.append(ticker)

        if (i + 1) % 50 == 0:
            print(f"  Fetched {i+1}/{len(tickers)} tickers")
            time.sleep(1)

    if failed_tickers:
        print(f"Failed to fetch: {len(failed_tickers)} tickers")

    print(f"Successfully fetched prices for {len(all_prices)} tickers")

    prices_df = pd.DataFrame(all_prices)
    prices_df.index = pd.to_datetime(prices_df.index)

    return prices_df, failed_tickers


In [ ]:
def get_price_on_date(prices_df, ticker, date, lookback_days=5):
    """Get close price for a ticker on a date (with lookback for non-trading days)."""
    date = pd.to_datetime(date)

    if ticker not in prices_df.columns:
        return None

    ticker_prices = prices_df[ticker].dropna()
    # Try exact date first
    if date in ticker_prices.index:
        return ticker_prices.loc[date]

    # Look back up to lookback_days
    for i in range(1, lookback_days + 1):
        check_date = date - timedelta(days=i)
        if check_date in ticker_prices.index:
            return ticker_prices.loc[check_date]
    return None

## Copy-cat portfolio

In [ ]:
class CopycatPortfolio:
    """Simulates a copy-cat portfolio following a legislator's trades.

    Key Logic:
    - Start with INITIAL_CAPITAL as cash
    - Initialize with existing positions from get_position(start_date)
    - Execute trades on Filed date using Filed date prices
    - Shares calculated as: Trade_Size_USD / Traded_date_price
    - Daily portfolio value = cash + sum(shares * current_price)
    """

    def __init__(self, congressman, prices_df):
        self.congressman = congressman
        self.prices_df = prices_df
        self.holdings = {}  # {ticker: shares}
        self.cash = INITIAL_CAPITAL
        self.history = []
        self.snapshots = {}  # {date_str: holdings_dict}

    def simulate(self, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
        """Run the day-by-day simulation."""
        start_dt = pd.to_datetime(start_date)
        end_dt = pd.to_datetime(end_date)

        # Reset state
        self.holdings = {}
        self.cash = INITIAL_CAPITAL

        # Initialize with starting positions from before simulation start
        initial_positions = self.congressman.get_position(start_dt)
        if initial_positions:
            print(f"    Initial positions: {len(initial_positions)} tickers")
            for ticker, dollar_amount in initial_positions.items():
                price = get_price_on_date(self.prices_df, ticker, start_dt)
                if price is not None and price > 0:
                    shares = dollar_amount / price
                    self.holdings[ticker] = shares
                    # Don't reduce cash - we're copying existing positions, not buying them

        # Check if there are any transactions
        if self.congressman.positions_df.empty:
            print(f"    No new transactions to simulate")
            # Still generate returns based on initial holdings
            return self._generate_daily_values(start_dt, end_dt)

        # Get transactions within simulation period (by Filed date)
        txs = self.congressman.positions_df.copy()
        txs['Filed'] = pd.to_datetime(txs['Filed'])
        txs = txs[(txs['Filed'] >= start_dt) & (txs['Filed'] <= end_dt)]

        if txs.empty:
            print(f"    No transactions in date range")
            return self._generate_daily_values(start_dt, end_dt)

        print(f"    Transactions in range: {len(txs)}")

        # Prepare transactions grouped by Filed date
        # Adjust weekend Filed dates to next business day (Monday)
        def adjust_to_next_business_day(d):
            d = pd.to_datetime(d)
            if d.weekday() == 5:  # Saturday -> Monday
                return (d + timedelta(days=2)).date()
            elif d.weekday() == 6:  # Sunday -> Monday
                return (d + timedelta(days=1)).date()
            return d.date()

        txs['Filed_date'] = txs['Filed'].apply(adjust_to_next_business_day)
        trades_by_date = txs.groupby('Filed_date')

        # Generate daily values with trade execution
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')  # Business days

        records = []
        initial_stock_value = None
        prev_stock_value = None

        for date in date_range:
            date_key = date.date()

            # Check if there are trades to execute on this date
            if date_key in trades_by_date.groups:
                day_trades = trades_by_date.get_group(date_key)
                self._execute_trades(day_trades, date)

            # Calculate stock holdings value
            stock_value = self._calculate_stock_holdings_value(date)

            # Cash invested = INITIAL_CAPITAL - current_cash
            cash_invested = INITIAL_CAPITAL - self.cash

            # Track initial stock value for cumulative return
            if initial_stock_value is None:
                initial_stock_value = stock_value

            # Cumulative return = (stock_value - initial_stock_value) / cash_invested
            if cash_invested > 0:
                cumulative_return = (stock_value - initial_stock_value) / cash_invested
            else:
                cumulative_return = 0

            # Log return (for plotting)
            if prev_stock_value is not None and prev_stock_value > 0 and stock_value > 0:
                log_return = np.log(stock_value / prev_stock_value)
            else:
                log_return = 0

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'cash': self.cash,
                'cash_invested': cash_invested,
                'portfolio_value': stock_value + self.cash,
                'cumulative_return': cumulative_return,
                'cumulative_return_pct': cumulative_return * 100,
                'log_return': log_return
            })

            prev_stock_value = stock_value

            # Capture snapshots
            date_str = date.strftime('%Y-%m-%d')
            if date_str in SNAPSHOT_DATES:
                self.snapshots[date_str] = self._get_current_holdings_in_dollars(date)

        df = pd.DataFrame(records)

        if not df.empty:
            # Cumulative log return (sum of daily log returns)
            df['cumulative_log_return'] = df['log_return'].cumsum()
        else:
            print(f"    WARNING: No records generated!")

        self.history = df
        return df

    def _generate_daily_values(self, start_dt, end_dt):
        """Generate daily portfolio values for portfolios with no new trades (uses initial holdings)."""
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')

        records = []
        initial_stock_value = None
        prev_stock_value = None

        for date in date_range:
            # Calculate stock holdings value
            stock_value = self._calculate_stock_holdings_value(date)
            cash_invested = INITIAL_CAPITAL - self.cash

            # Track initial stock value
            if initial_stock_value is None:
                initial_stock_value = stock_value

            # Cumulative return = (stock_value - initial_stock_value) / cash_invested
            if cash_invested > 0:
                cumulative_return = (stock_value - initial_stock_value) / cash_invested
            else:
                cumulative_return = 0

            # Log return (for plotting)
            if prev_stock_value is not None and prev_stock_value > 0 and stock_value > 0:
                log_return = np.log(stock_value / prev_stock_value)
            else:
                log_return = 0

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'cash': self.cash,
                'cash_invested': cash_invested,
                'portfolio_value': stock_value + self.cash,
                'cumulative_return': cumulative_return,
                'cumulative_return_pct': cumulative_return * 100,
                'log_return': log_return
            })

            prev_stock_value = stock_value

            # Capture snapshots
            date_str = date.strftime('%Y-%m-%d')
            if date_str in SNAPSHOT_DATES:
                self.snapshots[date_str] = self._get_current_holdings_in_dollars(date)

        df = pd.DataFrame(records)

        if not df.empty:
            # Cumulative log return (sum of daily log returns)
            df['cumulative_log_return'] = df['log_return'].cumsum()

        self.history = df
        return df

    def _execute_trades(self, day_trades, current_date):
        """Execute all trades for a given day."""
        for _, tx in day_trades.iterrows():
            ticker = tx['Ticker']
            traded_date = tx['Date']  # Traded date
            trade_size_usd = tx['Trade_Size_USD']
            is_buy = tx['Amount'] > 0

            # Calculate shares using Traded date price
            traded_price = get_price_on_date(self.prices_df, ticker, traded_date)

            # Execute at current (Filed) date price
            filed_price = get_price_on_date(self.prices_df, ticker, current_date)

            if traded_price is None or filed_price is None or traded_price <= 0 or filed_price <= 0:
                continue

            # Shares = Trade_Size_USD / Traded_date_price
            shares = trade_size_usd / traded_price

            if is_buy:
                # Buy shares at Filed price
                cost = shares * filed_price
                self.holdings[ticker] = self.holdings.get(ticker, 0) + shares
                self.cash -= cost
            else:
                # Sell shares at Filed price
                if ticker in self.holdings:
                    shares_to_sell = min(shares, self.holdings[ticker])
                    self.holdings[ticker] -= shares_to_sell
                    self.cash += shares_to_sell * filed_price

                    if self.holdings[ticker] <= 0.0001:
                        del self.holdings[ticker]

    def _calculate_portfolio_value(self, date):
        """Calculate total portfolio value on a given date."""
        portfolio_value = self.cash

        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                portfolio_value += shares * price

        return portfolio_value

    def _calculate_stock_holdings_value(self, date):
        """Calculate total value of stock holdings only (excluding cash)."""
        stock_value = 0

        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                stock_value += shares * price

        return stock_value

    def _get_current_holdings_in_dollars(self, date):
        """Get current holdings valued in dollars."""
        holdings = {}
        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price and price > 0:
                holdings[ticker] = shares * price
        return holdings

    def get_portfolio_breakdown(self, as_of_date=None):
        """Get detailed portfolio breakdown including cash at a specific date.

        Args:
            as_of_date: Optional date to check. If None, uses current state.
                        Note: For historical dates, you must run simulate() first.

        Returns:
            DataFrame with all positions including cash, with columns:
            Asset, Shares, Price, Value, Weight
        """
        if as_of_date:
            as_of = pd.to_datetime(as_of_date)
        else:
            as_of = None

        records = []
        total_stock_value = 0

        # Add stock holdings
        for ticker, shares in self.holdings.items():
            if as_of:
                price = get_price_on_date(self.prices_df, ticker, as_of)
            else:
                # Use most recent price
                if ticker in self.prices_df.columns:
                    price = self.prices_df[ticker].dropna().iloc[-1]
                else:
                    price = None

            if price and price > 0:
                value = shares * price
                total_stock_value += value
                records.append({
                    'Asset': ticker,
                    'Type': 'Stock',
                    'Shares': shares,
                    'Price': price,
                    'Value': value
                })

        # Add cash
        records.append({
            'Asset': 'CASH',
            'Type': 'Cash',
            'Shares': None,
            'Price': 1.0,
            'Value': self.cash
        })

        df = pd.DataFrame(records)
        total_value = df['Value'].sum()
        df['Weight'] = (df['Value'] / total_value * 100).round(2)
        df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Print summary
        print(f"\n{'='*70}")
        print(f"Portfolio Breakdown for {self.congressman.name}")
        if as_of_date:
            print(f"As of: {as_of_date}")
        print(f"{'='*70}")
        print(f"Total Portfolio Value: ${total_value:,.2f}")
        print(f"  - Stock Holdings:    ${total_stock_value:,.2f} ({total_stock_value/total_value*100:.1f}%)")
        print(f"  - Cash:              ${self.cash:,.2f} ({self.cash/total_value*100:.1f}%)")
        print(f"Number of Positions:   {len(self.holdings)}")
        print(f"{'='*70}\n")

        return df


In [ ]:
def get_spy_returns(start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """Get SPY benchmark returns."""
    spy = yf.download('SPY', start=start_date, end=end_date, progress=False)

    df = pd.DataFrame({
        'Date': spy.index,
        'Close': spy['Close'].values.flatten()
    })

    df['daily_return'] = df['Close'].pct_change()
    df['cumulative_return'] = (1 + df['daily_return'].fillna(0)).cumprod() - 1
    df['cumulative_return_pct'] = df['cumulative_return'] * 100

    # Log returns
    df['log_return'] = np.log(1 + df['daily_return']).replace([np.inf, -np.inf], 0).fillna(0)
    df['cumulative_log_return'] = df['log_return'].cumsum()

    return df


In [ ]:
congressmen = []
all_tickers = set()

for _, row in lawmakers.iterrows():
    congressman = Congressman_df(
        name=row['name'],
        party=row['party'],
        chamber=row['chamber'],
        state=row['state'],
        bioguide=row['bioguide'],
        trades_df=raw_df
    )
    congressmen.append(congressman)
    all_tickers.update(congressman.tickers)


In [ ]:
all_tickers.add('SPY')
prices_df, failed_tickers = fetch_prices(list(all_tickers))

Fetching prices for 1302 tickers...


ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['BPMP']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:HTTP Error 404: {"quoteSummary":{"result":null,"error":{"code":"Not Found","description":"Quote not found for symbol: PARA"}}}
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PARA']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['ABC']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['BKEP']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CCXI']: YFPricesMissingError('possibly delisted; no price data found  (1d 2018-12-04 00:00:00 -> 2025-01-07 00:00:00)')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['DLPH']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['BGFV']: YFTzMissingError('possibly delisted; no ti

  Fetched 50/1302 tickers


ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['DNHBY']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PEAK']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['SPKEP']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PEGI']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['ASXC']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['VMW']: YFTzMissingError('possibly delisted; no timezone found')


  Fetched 100/1302 tickers


...

  Fetched 1200/1302 tickers


ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['GPP']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['HDS']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PRAH']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PBFX']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CCXX']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CRY']: YFTzMissingError('possibly delisted; no timezone found')


  Fetched 1250/1302 tickers


ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PXD']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['HES']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['CEB']: YFPricesMissingError('possibly delisted; no price data found  (1d 2018-12-04 00:00:00 -> 2025-01-07 00:00:00)')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['PSXP']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['AESE']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['VRTU']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['SYMBOL']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfinance:
1 Failed download:
ERROR:yfinance:['ARNC']: YFTzMissingError('possibly delisted; no timezone found')
ERROR:yfin

  Fetched 1300/1302 tickers
Failed to fetch: 236 tickers
Successfully fetched prices for 1066 tickers


In [ ]:
spy_returns = get_spy_returns()

In [ ]:
portfolios = {}
copycat_objects = {}

for congressman in congressmen:
    if congressman.transactions is None:
        continue

    print(f"  Simulating: {congressman.name}")
    copycat = CopycatPortfolio(congressman, prices_df)
    result = copycat.simulate()

    if result is not None and len(result) > 0:
        portfolios[congressman.name] = result
        copycat_objects[congressman.name] = copycat

  Simulating: Josh Gottheimer
    Initial positions: 70 tickers
    Transactions in range: 2506
  Simulating: Nancy Pelosi
    Initial positions: 1 tickers
    Transactions in range: 44
  Simulating: Kevin Hern
    Initial positions: 1 tickers
    Transactions in range: 659
  Simulating: Mark Green
    Transactions in range: 618
  Simulating: Bradley S. Schneider
    Initial positions: 5 tickers
    Transactions in range: 50
  Simulating: Virginia Foxx
    Initial positions: 14 tickers
    Transactions in range: 610
  Simulating: Kim Schrier
    Transactions in range: 41
  Simulating: Mikie Sherrill
    Transactions in range: 292
  Simulating: Daniel Meuser
    Transactions in range: 59
  Simulating: Susie Lee
    Transactions in range: 1257
  Simulating: John W. Rose
    Transactions in range: 9
  Simulating: Brian Mast
    Initial positions: 2 tickers
    Transactions in range: 83
  Simulating: Carol Devine Miller
    Transactions in range: 103
  Simulating: Michael C. Burgess
    Tr

## Visualization

In [ ]:
mapping = {
    'AA': 'Materials', 'AAGIY': 'Financials', 'AAIGF': 'Financials', 'AAL': 'Industrials', 'AAP': 'Consumer Discretionary',
    'AAPL': 'Technology', 'AB': 'Financials', 'ABBV': 'Healthcare', 'ABCB': 'Financials', 'ABEV': 'Consumer Staples',
    'ABG': 'Consumer Discretionary', 'ABNB': 'Consumer Discretionary', 'ABMD': 'Healthcare', 'ABYIX': 'Fund',
    'ACHC': 'Healthcare', 'ACI': 'Consumer Staples', 'ACIW': 'Technology', 'ACM': 'Industrials', 'ACN': 'Technology',
    'ADBE': 'Technology', 'ADC': 'Real Estate', 'ADDYY': 'Financials', 'ADI': 'Technology', 'ADM': 'Materials',
    'ADP': 'Technology', 'ADSK': 'Technology', 'ADYEY': 'Technology', 'AEE': 'Utilities', 'AEG': 'Financials',
    'AEIS': 'Industrials', 'AEP': 'Utilities', 'AES': 'Utilities', 'AFL': 'Financials', 'AFRM': 'Financials',
    'AGAE': 'Communication Services', 'AGCO': 'Industrials', 'AGIO': 'Healthcare', 'AGX': 'Industrials', 'AHCO': 'Healthcare',
    'AHKSY': 'Industrials', 'AHT': 'Real Estate', 'AI': 'Technology', 'AIG': 'Financials', 'AIO': 'Financials',
    'AIQUY': 'Materials', 'AIR': 'Industrials', 'AJG': 'Financials', 'AKAM': 'Technology', 'ALB': 'Materials',
    'ALC': 'Healthcare', 'ALFVY': 'Industrials', 'ALG': 'Industrials', 'ALGM': 'Technology', 'ALGN': 'Healthcare',
    'ALGT': 'Industrials', 'ALIZY': 'Financials', 'ALK': 'Industrials', 'ALL': 'Financials', 'ALLY.A': 'Financials',
    'ALNY': 'Healthcare', 'AM': 'Energy', 'AMADY': 'Technology', 'AMAT': 'Technology', 'AMC': 'Communication Services',
    'AMD': 'Technology', 'AME': 'Industrials', 'AMGN': 'Healthcare', 'AMLP': 'ETF', 'AMP': 'Financials',
    'AMRC': 'Industrials', 'AMRX': 'Healthcare', 'AMSF': 'Financials', 'AMT': 'Real Estate', 'AMTD': 'Financials',
    'AMTX': 'Materials', 'AMWD': 'Industrials', 'AMZA': 'ETF', 'AMZN': 'Consumer Discretionary', 'ANET': 'Technology',
    'AON': 'Financials', 'AORT': 'Healthcare', 'AOS': 'Industrials', 'APA': 'Energy', 'APD': 'Materials',
    'APH': 'Technology', 'APNHY': 'Healthcare', 'APO': 'Financials', 'APP': 'Communication Services', 'APPF': 'Technology',
    'APU': 'Utilities', 'AQN': 'Utilities', 'AQUA': 'Utilities', 'ARCB': 'Industrials', 'ARCC': 'Financials', 'ARE': 'Real Estate',
    'ARKK': 'ETF', 'ARLP': 'Energy', 'ARMK': 'Consumer Discretionary', 'AROC': 'Energy', 'ARQT': 'Healthcare',
    'ASAZY': 'Industrials', 'ASC': 'Industrials', 'ASIX': 'Materials', 'ASML': 'Technology', 'ASXC': 'Materials',
    'ATKR': 'Industrials', 'ATLKY': 'Industrials', 'ATOAX': 'ETF', 'ATR': 'Healthcare', 'ATRC': 'Healthcare', 'AUY': 'Materials',
    'AVB': 'Real Estate', 'AVGO': 'Technology', 'AVNT': 'Materials', 'AVT': 'Industrials', 'AVTR': 'Healthcare', 'AVY': 'Materials',
    'AWK': 'Utilities', 'AXHE': 'Technology', 'AXP': 'Financials', 'AXS': 'Financials', 'AYR': 'Industrials', 'AZEK': 'Materials',
    'AZN': 'Healthcare', 'AZO': 'Consumer Discretionary', 'AZSEY': 'Financials', 'BAMXY': 'Financials', 'BECN': 'Industrials',
    'BERY': 'Materials', 'BGFV': 'Consumer Discretionary', 'BGNE': 'Healthcare', 'BHI': 'Industrials', 'BKEP': 'Energy',
    'BKI': 'Financials', 'BLL': 'Materials', 'BLUE': 'Consumer Discretionary', 'BPL': 'Energy', 'BPMP': 'Financials',
    'BRK.B': 'Financials', 'BRKS': 'Technology', 'CAA': 'Consumer Discretionary', 'CACI': 'Technology', 'CALD': 'Industrials',
    'CATM': 'Technology', 'CBM': 'Materials', 'CBS': 'Communication Services', 'CCMP': 'Materials', 'CCT': 'Real Estate',
    'CCXI': 'Healthcare', 'CCXX': 'Materials', 'CDK': 'Technology', 'CEB': 'Technology', 'CEQP': 'Energy', 'CERN': 'Healthcare',
    'CHL': 'Materials', 'CHNG': 'Financials', 'CHUY': 'Consumer Discretionary', 'CHX': 'Financials', 'CINR': 'Industrials',
    'CLNC': 'Healthcare', 'CLR': 'Energy', 'CMD': 'Materials', 'CNXM': 'Technology', 'CONE': 'Communication Services',
    'COT': 'Energy', 'COTV': 'Energy', 'CREE': 'Technology', 'CRY': 'Healthcare', 'CTL': 'Communication Services',
    'CTLT': 'Healthcare', 'CTRA': 'Consumer Discretionary', 'CTRM': 'Energy', 'CTXS': 'Technology', 'CVET': 'Healthcare',
    'CWEN.A': 'Utilities', 'CWST': 'Industrials', 'DAIUF': 'Financials', 'DANOY': 'Healthcare', 'DASTY': 'Financials',
    'DBRG': 'Financials', 'DBSDY': 'Financials', 'DCI': 'Industrials', 'DCO': 'Energy', 'DCP': 'Energy', 'DE': 'Industrials',
    'DFKCY': 'Financials', 'DFS': 'Financials', 'DG': 'Consumer Discretionary', 'DHI': 'Consumer Discretionary',
    'DIAL': 'Consumer Discretionary', 'DIFTY': 'Technology', 'DIN': 'Consumer Discretionary', 'DISCA': 'Communication Services',
    'DLPH': 'Industrials', 'DNB': 'Financials', 'DNHBY': 'Financials', 'DNKN': 'Consumer Discretionary', 'DNTUY': 'Financials',
    'DORM': 'Consumer Discretionary', 'DOV': 'Industrials', 'DOW': 'Materials', 'DOX': 'Technology', 'DPLO': 'Financials',
    'DRE': 'Real Estate', 'DRQ': 'Healthcare', 'DSCSY': 'Financials', 'DSDVY': 'Financials', 'DSEY': 'Consumer Discretionary',
    'DSGX': 'Financials', 'DTE': 'Energy', 'DTM': 'Materials', 'DUK': 'Utilities', 'DUKH': 'Utilities', 'DUSA': 'Financials',
    'DVN': 'Energy', 'EADSY': 'Financials', 'EBS': 'Financials', 'EBSB': 'Financials', 'ECOL': 'Materials', 'EDR': 'Energy',
    'EFA': 'ETF', 'EFC': 'Financials', 'EHC': 'Healthcare', 'ELAN': 'Healthcare', 'EMXC': 'ETF', 'ENB': 'Energy',
    'ENBL': 'Technology', 'ENLAY': 'Financials', 'ENLC': 'Energy', 'ENR': 'Energy', 'ENTG': 'Technology', 'ENV': 'Energy',
    'EOG': 'Energy', 'EPAC': 'Financials', 'EPD': 'Energy', 'EPOKY': 'Financials', 'ERI': 'Technology', 'ERJ': 'Industrials',
    'ESGC': 'ETF', 'ESI': 'Healthcare', 'ESL': 'Financials', 'ESLOY': 'Financials', 'ESRX': 'Healthcare', 'ESTC': 'Technology',
    'ET': 'Utilities', 'ETR': 'Utilities', 'ETRN': 'Industrials', 'ETV': 'Industrials', 'EW': 'Healthcare', 'EWBC': 'Financials',
    'EXAS': 'Healthcare', 'EXC': 'Utilities', 'EXLS': 'Technology', 'EXPD': 'Industrials', 'EXPE': 'Consumer Discretionary',
    'EYE': 'Healthcare', 'FAF': 'Financials', 'FANUF': 'Industrials', 'FANUY': 'Industrials', 'FAS': 'Financials', 'FAST': 'Consumer Discretionary',
    'FCX': 'Materials', 'FDC': 'Financials', 'FDEV': 'Technology', 'FDIS': 'ETF', 'FDRR': 'Financials', 'FDS': 'Technology',
    'FDX': 'Industrials', 'FE': 'Utilities', 'FET': 'Technology', 'FEYE': 'Technology', 'FF': 'Energy', 'FHB': 'Financials',
    'FHLC': 'Financials', 'FHN': 'Financials', 'FHYS': 'Financials', 'FI': 'Financials', 'FICO': 'Technology', 'FIVE': 'Consumer Discretionary',
    'FLIR': 'Technology', 'FLL': 'Energy', 'FLNG': 'Energy', 'FLO': 'Consumer Discretionary', 'FLT': 'Industrials',
    'FLYW': 'Industrials', 'FMAT': 'Materials', 'FMC': 'Materials', 'FMS': 'Industrials', 'FMX': 'Materials', 'FNA': 'Financials',
    'FND': 'Consumer Discretionary', 'FNSXX': 'ETF', 'FNV': 'Materials', 'FOUR': 'Financials', 'FOXF': 'Communication Services',
    'FQAL': 'ETF', 'FRC': 'Financials', 'FSK': 'Energy', 'FSKR': 'Energy', 'FSLR': 'Technology', 'FSMDX': 'ETF', 'FSP': 'Financials',
    'FTEC': 'ETF', 'FTK': 'Industrials', 'FTSM': 'Financials', 'FUPBY': 'Financials', 'FVRR': 'Technology', 'FWRG': 'Financials',
    'GBCI': 'Financials', 'GBOOY': 'Financials', 'GCGMF': 'Financials', 'GD': 'Industrials', 'GDDY': 'Technology', 'GDEN': 'Energy',
    'GE': 'Industrials', 'GEL': 'Energy', 'GFL': 'Industrials', 'GGT': 'Materials', 'GH': 'Healthcare', 'GLD': 'ETF',
    'GLIBA': 'Healthcare', 'GLOB': 'Consumer Discretionary', 'GLOP': 'Energy', 'GLP': 'Real Estate', 'GLW': 'Technology',
    'GMAB': 'Healthcare', 'GME': 'Consumer Discretionary', 'GMED': 'Healthcare', 'GMLP': 'Energy', 'GMXAY': 'Financials',
    'GO': 'Technology', 'GOGL': 'Communication Services', 'GPK': 'Materials', 'GPN': 'Technology', 'GPP': 'Energy', 'GRUB': 'Consumer Discretionary',
    'GSK': 'Healthcare', 'GT': 'Industrials', 'GTES': 'Energy', 'GTLS': 'Industrials', 'GTX': 'Industrials', 'GVDNY': 'Financials',
    'GWW': 'Industrials', 'GXO': 'Industrials', 'HACK': 'ETF', 'HAE': 'Healthcare', 'HAIN': 'Consumer Staples', 'HAL': 'Energy',
    'HALO': 'Healthcare', 'HAS': 'Consumer Discretionary', 'HASI': 'Utilities', 'HBAN': 'Financials', 'HCP': 'Real Estate',
    'HCRB': 'Financials', 'HDB': 'Financials', 'HDS': 'Industrials', 'HEI': 'Consumer Discretionary', 'HEI.A': 'Consumer Discretionary',
    'HELE': 'Industrials', 'HES': 'Energy', 'HESAY': 'Energy', 'HESM': 'Energy', 'HFC': 'Energy', 'HHC': 'Financials',
    'HIBB': 'Consumer Discretionary', 'HIG': 'Financials', 'HKXCY': 'Financials', 'HLI': 'Financials', 'HLIO': 'Healthcare',
    'HLMN': 'Healthcare', 'HLN': 'Consumer Discretionary', 'HLT': 'Consumer Discretionary', 'HMN': 'Healthcare', 'HNDL': 'ETF',
    'HOCPY': 'Energy', 'HOLX': 'Healthcare', 'HPP': 'Real Estate', 'HPQ': 'Technology', 'HPT': 'Real Estate', 'HQY': 'Technology',
    'HRB': 'Consumer Discretionary', 'HRC': 'Materials', 'HRI': 'Consumer Discretionary', 'HRL': 'Consumer Staples', 'HRS': 'Industrials',
    'HSBC': 'Financials', 'HSHCY': 'Financials', 'HSIC': 'Healthcare', 'HST': 'Real Estate', 'HSY': 'Consumer Staples', 'HTGC': 'Financials',
    'HTLD': 'Industrials', 'HUBB': 'Industrials', 'HUBS': 'Technology', 'HUM': 'Healthcare', 'HUN': 'Materials', 'HXL': 'Materials',
    'HZN': 'Industrials', 'IAA': 'Industrials', 'IART': 'Healthcare', 'IAU': 'ETF', 'IBDRY': 'Financials', 'IBKC': 'Financials',
    'IBKR': 'Financials', 'IBN': 'Healthcare', 'IBP': 'Consumer Staples', 'ICE': 'Financials', 'ICFI': 'Technology', 'ICLR': 'Healthcare',
    'ICUI': 'Healthcare', 'IDA': 'ETF', 'IFF': 'Materials', 'IFNNY': 'Financials', 'IGSB': 'ETF', 'IGV': 'Technology',
    'IHG': 'Consumer Discretionary', 'IHS': 'Industrials', 'IJR': 'ETF', 'ILMN': 'Healthcare', 'ILPT': 'Real Estate',
    'IMAX': 'Communication Services', 'IMBBY': 'Healthcare', 'IMKTA': 'Consumer Staples', 'INDA': 'ETF', 'INDB': 'Financials',
    'INFO': 'Technology', 'INSM': 'Healthcare', 'INTA': 'Consumer Discretionary', 'INTU': 'Technology', 'IP': 'Materials',
    'IPWR': 'Technology', 'IPXL': 'Healthcare', 'IQV': 'Healthcare', 'IR': 'Materials', 'IRM': 'Industrials', 'IRT': 'Technology',
    'ISRG': 'Healthcare', 'IT': 'Technology', 'ITCI': 'Healthcare', 'ITIP': 'Technology', 'ITT': 'Industrials', 'ITUB': 'Financials',
    'ITW': 'Industrials', 'IVW': 'ETF', 'IVZ': 'Financials', 'IWM': 'ETF', 'IWN': 'ETF', 'IXJ': 'ETF', 'IYZ': 'ETF', 'J': 'Technology',
    'JBL': 'Consumer Discretionary', 'JBT': 'Industrials', 'JCI': 'Industrials', 'JEPI': 'ETF', 'JGCCY': 'Financials', 'JLL': 'Real Estate',
    'JMHLY': 'Healthcare', 'JOE': 'Consumer Discretionary', 'K': 'Consumer Staples', 'KAI': 'Technology', 'KAR': 'Consumer Discretionary',
    'KBCSY': 'Financials', 'KBH': 'Consumer Discretionary', 'KD': 'Consumer Staples', 'KEY': 'Financials', 'KEYS': 'Technology',
    'KHC': 'Consumer Staples', 'KKPNY': 'Financials', 'KKR': 'Financials', 'KLAC': 'Technology', 'KMB': 'Consumer Staples',
    'KMI': 'Energy', 'KMTUY': 'Materials', 'KMX': 'Consumer Discretionary', 'KNOP': 'Energy', 'KOSCF': 'Energy', 'KR': 'Consumer Staples',
    'KS': 'Industrials', 'KUBTY': 'Financials', 'KVUE': 'Communication Services', 'KYCCF': 'Financials', 'KYN': 'Financials',
    'L': 'Consumer Discretionary', 'LAD': 'Financials', 'LAMR': 'Industrials', 'LAND': 'Real Estate', 'LBDAV': 'Financials',
    'LBRDA': 'Financials', 'LBRDK': 'Financials', 'LDNXF': 'Energy', 'LDOS': 'Technology', 'LEA': 'Industrials', 'LEG': 'Consumer Discretionary',
    'LESL': 'Consumer Discretionary', 'LH': 'Healthcare', 'LHCG': 'Healthcare', 'LHX': 'Industrials', 'LIN': 'Materials', 'LITE': 'Technology',
    'LKQ': 'Consumer Discretionary', 'LLDTF': 'Financials', 'LLL': 'Healthcare', 'LLY': 'Healthcare', 'LNEGY': 'Energy', 'LNG': 'Energy',
    'LNT': 'Utilities', 'LOGM': 'Technology', 'LOPE': 'Consumer Discretionary', 'LOW': 'Consumer Discretionary', 'LPLA': 'Materials',
    'LRCX': 'Technology', 'LRLCY': 'Financials', 'LSXMK': 'ETF', 'LTD': 'Consumer Discretionary', 'LTHM': 'Materials', 'LULU': 'Consumer Discretionary',
    'LUMN': 'Communication Services', 'LUMO': 'Technology', 'LUMN': 'Communication Services', 'LUV': 'Industrials', 'LW': 'Industrials',
    'LYB': 'Materials', 'LYG': 'Financials', 'LYV': 'Communication Services', 'LYV': 'Communication Services', 'M': 'Consumer Discretionary',
    'MA': 'Financials', 'MAC': 'Financials', 'MAS': 'Industrials', 'MATX': 'Industrials', 'MBI': 'Financials', 'MBT': 'Financials',
    'MC': 'Financials', 'MCD': 'Consumer Discretionary', 'MCK': 'Healthcare', 'MD': 'Healthcare', 'MDLZ': 'Consumer Staples',
    'MELI': 'Consumer Discretionary', 'META': 'Communication Services', 'MET': 'Financials', 'MGM': 'Consumer Discretionary',
    'MHK': 'Consumer Discretionary', 'MJN': 'Consumer Staples', 'MKC': 'Consumer Staples', 'MKL': 'Financials', 'MKTX': 'Technology',
    'MLM': 'Materials', 'MMC': 'Financials', 'MMM': 'Industrials', 'MNST': 'Consumer Staples', 'MO': 'Consumer Staples',
    'MODN': 'Healthcare', 'MOH': 'Healthcare', 'MON': 'Materials', 'MOS': 'Materials', 'MOV': 'Consumer Discretionary', 'MP': 'Energy',
    'MPW': 'Real Estate', 'MRK': 'Healthcare', 'MRO': 'Energy', 'MSFT': 'Technology', 'MSI': 'Technology', 'MTB': 'Financials',
    'MTCH': 'Communication Services', 'MTD': 'Healthcare', 'MTN': 'Financials', 'MU': 'Technology', 'MUR': 'Energy', 'MXIM': 'Technology',
    'MYGN': 'Healthcare', 'NBL': 'Energy', 'NDAQ': 'Financials', 'NEE': 'Utilities', 'NEP': 'Utilities', 'NET': 'Technology',
    'NFLX': 'Communication Services', 'NKE': 'Consumer Discretionary', 'NLOK': 'Technology', 'NOC': 'Industrials', 'NOV': 'Energy',
    'NOW': 'Technology', 'NP': 'Financials', 'NPTN': 'Technology', 'NRG': 'Utilities', 'NRZ': 'Financials', 'NSC': 'Industrials',
    'NSRGY': 'Consumer Staples', 'NTAP': 'Technology', 'NTES': 'Technology', 'NVDA': 'Technology', 'NVO': 'Healthcare', 'NVR': 'Consumer Discretionary',
    'NWL': 'Consumer Staples', 'NWSA': 'Communication Services', 'NXPI': 'Technology', 'NYCB': 'Financials', 'NYMT': 'Financials',
    'O': 'Real Estate', 'OC': 'Financials', 'ODFL': 'Industrials', 'OGN': 'Energy', 'OKE': 'Energy', 'OMC': 'Consumer Discretionary',
    'ON': 'Healthcare', 'ONB': 'Financials', 'ORCL': 'Technology', 'ORLY': 'Consumer Discretionary', 'OXY': 'Energy', 'PAA': 'Energy',
    'PACD': 'Industrials', 'PANW': 'Technology', 'PAR': 'Consumer Discretionary', 'PAYX': 'Technology', 'PBCT': 'Financials',
    'PBF': 'Energy', 'PCAR': 'Industrials', 'PCLN': 'Consumer Discretionary', 'PDCO': 'Healthcare', 'PEAK': 'Financials',
    'PEG': 'Utilities', 'PEGA': 'Technology', 'PEP': 'Consumer Staples', 'PFE': 'Healthcare', 'PG': 'Consumer Staples',
    'PGR': 'Financials', 'PH': 'Industrials', 'PHG': 'Technology', 'PHM': 'Consumer Discretionary', 'PKG': 'Materials',
    'PKI': 'Healthcare', 'PLD': 'Real Estate', 'PLNT': 'Consumer Discretionary', 'PLUG': 'Energy', 'PM': 'Consumer Staples',
    'PNC': 'Financials', 'PNR': 'Industrials', 'PNW': 'Utilities', 'POOL': 'Consumer Discretionary', 'PPG': 'Materials',
    'PPL': 'Utilities', 'PRGO': 'Healthcare', 'PRU': 'Financials', 'PSA': 'Real Estate', 'PSX': 'Energy', 'PTC': 'Technology',
    'PTON': 'Consumer Discretionary', 'PUBGY': 'Financials', 'PVH': 'Consumer Discretionary', 'PWR': 'Industrials', 'PXD': 'Energy',
    'PYPL': 'Technology', 'QCOM': 'Technology', 'QRTEA': 'Technology', 'QSR': 'Consumer Discretionary', 'R': 'Consumer Discretionary',
    'RACE': 'Consumer Discretionary', 'RCL': 'Consumer Discretionary', 'RE': 'Financials', 'REG': 'Industrials', 'REGN': 'Healthcare',
    'RF': 'Financials', 'RHI': 'Industrials', 'RIG': 'Energy', 'RIO': 'Materials', 'RIVN': 'Consumer Discretionary', 'RL': 'Consumer Discretionary',
    'ROK': 'Industrials', 'ROP': 'Industrials', 'ROST': 'Consumer Discretionary', 'RPRX': 'Healthcare', 'RPM': 'Materials',
    'RPRX': 'Healthcare', 'RS': 'Technology', 'RSG': 'Industrials', 'RTX': 'Industrials', 'RUN': 'Utilities', 'RY': 'Financials',
    'SBUX': 'Consumer Discretionary', 'SCHW': 'Financials', 'SEE': 'Industrials', 'SHW': 'Materials', 'SIRI': 'Communication Services',
    'SIVB': 'Financials', 'SJM': 'Consumer Staples', 'SLB': 'Energy', 'SLG': 'Real Estate', 'SMG': 'Consumer Discretionary',
    'SNA': 'Industrials', 'SNOW': 'Technology', 'SNPS': 'Technology', 'SO': 'Utilities', 'SPG': 'Real Estate', 'SPGI': 'Financials',
    'SPLK': 'Technology', 'SPOT': 'Technology', 'SPWR': 'Utilities', 'SQ': 'Technology', 'SQM': 'Materials', 'SRCL': 'Industrials',
    'SRE': 'Utilities', 'STAG': 'Real Estate', 'STLD': 'Materials', 'STT': 'Financials', 'STX': 'Technology', 'STZ': 'Consumer Staples',
    'SU': 'Energy', 'SWKS': 'Technology', 'SYK': 'Healthcare', 'SYF': 'Financials', 'SYY': 'Consumer Staples', 'T': 'Communication Services',
    'TAP': 'Consumer Staples', 'TDC': 'Technology', 'TDG': 'Industrials', 'TDY': 'Industrials', 'TECH': 'Technology', 'TEL': 'Technology',
    'TER': 'Healthcare', 'TEX': 'Materials', 'TFX': 'Healthcare', 'TGT': 'Consumer Discretionary', 'TJX': 'Consumer Discretionary',
    'TMUS': 'Communication Services', 'TMO': 'Healthcare', 'TPR': 'Consumer Discretionary', 'TRMB': 'Technology', 'TRN': 'Industrials',
    'TRP': 'Energy', 'TRV': 'Financials', 'TSLA': 'Consumer Discretionary', 'TSM': 'Technology', 'TT': 'Industrials', 'TTD': 'Technology',
    'TTE': 'Energy', 'TTMI': 'Technology', 'TWTR': 'Communication Services', 'TXN': 'Technology', 'TXT': 'Industrials', 'TYL': 'Industrials',
    'UA': 'Consumer Discretionary', 'UAA': 'Consumer Discretionary', 'UAL': 'Industrials', 'UDR': 'Real Estate', 'UHS': 'Healthcare',
    'UHT': 'Real Estate', 'ULTA': 'Consumer Discretionary', 'UNH': 'Healthcare', 'UNM': 'Financials', 'UNP': 'Industrials',
    'UPS': 'Industrials', 'URI': 'Industrials', 'USB': 'Financials', 'V': 'Financials', 'VFC': 'Consumer Discretionary', 'VICI': 'Real Estate',
    'VLO': 'Energy', 'VMC': 'Materials', 'VNO': 'Real Estate', 'VTR': 'Real Estate', 'VZ': 'Communication Services', 'WAB': 'Industrials',
    'WAT': 'Industrials', 'WBA': 'Consumer Staples', 'WDC': 'Technology', 'WEC': 'Utilities', 'WELL': 'Real Estate', 'WES': 'Industrials',
    'WFC': 'Financials', 'WHR': 'Consumer Discretionary', 'WM': 'Industrials', 'WMB': 'Energy', 'WMT': 'Consumer Staples', 'WRB': 'Financials',
    'WRK': 'Industrials', 'WRLD': 'Technology', 'WU': 'Financials', 'WYNN': 'Consumer Discretionary', 'XEL': 'Utilities', 'XOM': 'Energy',
    'XRAY': 'Healthcare', 'XYL': 'Industrials', 'YUM': 'Consumer Discretionary', 'ZBH': 'Healthcare', 'ZBRA': 'Technology',
    'ZION': 'Financials', 'ZM': 'Technology', 'ZS': 'Technology', 'ZTS': 'Healthcare',    'BP': 'Energy',
    'CCI': 'Real Estate',
    'CMCSA': 'Communication Services',
    'DIS': 'Communication Services',
    'TTWO': 'Communication Services',
    'DXCM': 'Healthcare',
    'BEP': 'Utilities',
    'TDOC': 'Healthcare',
    'GS': 'Financials',
    'ALLY': 'Financials',
    'MS': 'Financials',
    'EL': 'Consumer Staples',
    'CYRX': 'Healthcare',
    'COST': 'Consumer Staples',
    'JPM': 'Financials',
    'CDNS': 'Technology',
    'LVMHF': 'Consumer Discretionary',
    'CGNX': 'Technology',
    'NTLA': 'Healthcare',
    'MSCI': 'Financials',
    'USO': 'ETF',
    'ECL': 'Materials',
    'BROS': 'Consumer Discretionary',
    'F': 'Consumer Discretionary',
    'NWN': 'Utilities',
    'WY': 'Financials',
    'COHR': 'Technology',
    'INTC': 'Technology',
    'HD': 'Consumer Discretionary',
    'BX': 'Financials',
    'GILD': 'Healthcare',
    'BLK': 'Financials',
    'BAC': 'Financials',
    'CVS': 'Consumer Staples',
    'CSCO': 'Technology',
    'CRM': 'Technology',
    'CAT': 'Industrials',
    'DGX': 'Healthcare',
    'JNJ': 'Healthcare',
    'CB': 'Financials',
    'C': 'Financials',
    'MDT': 'Healthcare',
    'SAP': 'Technology',
    'VOD': 'Communication Services',
    'POR': 'Utilities',
    'UL': 'Consumer Staples',
    'NEM': 'Materials',
    'MEOH': 'Materials',
    'FLEX': 'Technology',
    'BWA': 'Consumer Discretionary',
    'DD': 'Materials',
    'SWK': 'Industrials',
    'CI': 'Healthcare',
    'D': 'Utilities',
    'FLR': 'Industrials',
    'WWD': 'Consumer Discretionary',
    'CME': 'Financials',
    'MPC': 'Energy',
    'HON': 'Industrials',
    'GOOG': 'Technology',
    'LVMUY': 'Consumer Discretionary',
    'RHHBF': 'Healthcare',
    'DLTR': 'Consumer Discretionary',
    'ABTSTLA': 'Healthcare',
    'BTI': 'Consumer Staples',
    'CVX': 'Energy',
    'EMR': 'Industrials',
    'ABT': 'Healthcare',
    'SHY': 'ETF',
    'VUG': 'ETF',
    'YETI': 'Consumer Discretionary',
    'UBER': 'Technology',
    'SPCE': 'Consumer Discretionary',
    'SNAP': 'Communication Services',
    "LMT": "Aerospace & Defense",
    "RHHBY": "Pharmaceuticals",
    "OLP": "Real Estate / Investment Trust",
    "LZAGY": "Chemicals / Industrial Materials",
    "BEN": "Financial Services / Asset Management",
    "MFC": "Financial Services / Insurance"
}


In [ ]:
def plot_summary(portfolio_df, spy_df, legislator_name, INDUSTRY_MAP, snapshots, plottype="", save_path=None):

    # -------------------------
    # SUBPLOTS LAYOUT (4 ROWS, 3 COLS)
    # -------------------------
    fig = make_subplots(
        rows=4, cols=3,
        specs=[
            [{"colspan": 3}, None, None],  # Row 1: Line chart
            [None, None, None],            # Row 2: Empty spacer
            [{"type": "domain"}]*3,        # Row 3: Sunbursts
            [{"type": "domain"}]*3         # Row 4: Sunbursts
        ],
        row_heights=[0.4, 0.05, 0.275, 0.275],
        vertical_spacing=0.05,
        horizontal_spacing=0.03,
        subplot_titles=["Cumulative Returns"] + list(snapshots.keys()) # Limit titles to match available slots
    )

    # -------------------------
    # LINE PLOT
    # -------------------------
    # Portfolio returns
    fig.add_trace(go.Scatter(
        x=portfolio_df['Date'],
        y=portfolio_df['cumulative_return_pct'],
        mode='lines',
        name=f'{legislator_name} Portfolio vs SPY',
        line=dict(width=2)
    ))


    # SPY returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_return_pct'],
        mode='lines',
        name='SPY',
        line=dict(width=2, dash='dash', color='gray')
    ))


    fig.update_xaxes(title_text="Date",
                      row=1, col=1)
    fig.update_yaxes(
        title_text='Cumulative Return (%)'
,
        row=1, col=1
      )

    fig.update_layout(
        legend=dict(
            orientation="v",      # vertical or "h" if you prefer horizontal
            x=0.02,               # position on x-axis (0=left, 1=right)
            y=0.98,               # position on y-axis (0=bottom, 1=top)
            xanchor="left",      # anchors the legend box
            yanchor="top",
            bgcolor="rgba(255,255,255,0.7)",  # semi-transparent background

        )
    )

    # Use SNAPSHOT_DATES from global scope for subplot titles and iteration
    # Note: SNAPSHOT_DATES is already defined as a list of strings

    # -------------------------
    # SUNBURSTS (rows 3 & 4)
    # -------------------------

    for i, date_str in enumerate(snapshots.keys()): # Iterate only over the first 6 snapshots
        if date_str not in snapshots:
            print(f"Warning: Snapshot for {date_str} not found for {legislator_name}. Skipping.")
            continue
        w = snapshots[date_str]
        df = pd.Series(w).rename("Weight").reset_index().rename(columns={"index": "Ticker"})
        df["Industry"] = df["Ticker"].map(INDUSTRY_MAP)
        df["Industry"] = df["Industry"].fillna("Unknown")
        df = df[df["Weight"] > 0]
        if df.empty:
            continue

        sunburst = px.sunburst(
            df,
            path=["Industry", "Ticker"],
            values="Weight",
            color="Industry"
        )
        sunburst.update_traces(
            textinfo="label+percent parent",
            hovertemplate="<b>%{label}</b><br>%{value:.2%}<extra></extra>"
        )

        # Calculate row/col for sunbursts (row 3 & 4)
        row = (i // 3) + 3  # starts at row 3
        col = (i % 3) + 1
        fig.add_trace(sunburst.data[0], row=row, col=col)

    # -------------------------
    # Sunburst subtitle
    # -------------------------
    fig.add_annotation(
        text="Yearly Weighted Portfolio",
        x=0.5,
        y=0.6,  # centered between line chart and sunbursts
        xref="paper",
        yref="paper",
        showarrow=False,
        font=dict(size=16)
    )

    # -------------------------
    # Layout tweaks
    # -------------------------
    fig.update_layout(
        height=1800,  # taller to fill page
        width=1200,
        title_text=f"{legislator_name}<br>Cumulative {plottype} Portfolio Performance", # Use legislator_name instead of undefined congressman.name
        showlegend=True,
        margin=dict(t=100, l=50, r=50, b=50),
        hovermode="x unified",
        plot_bgcolor="rgba(245,245,245,0.6)",
        paper_bgcolor="white"
    )

    # -------------------------
    # Save figure dynamically
    # -------------------------
    safe_name = re.sub(r'[^0-9a-zA-Z_]', '', legislator_name.replace(" ", "_")) # Use legislator_name
    filename = f"{safe_name}_summary.html"
    if save_path:
      fig.write_html(os.path.join(save_path, filename))

    fig.show()


In [ ]:
summary_dir = os.path.join(OUTPUT_DIR, 'summary')
os.makedirs(summary_dir, exist_ok=True)

# Iterate over the portfolios dictionary
for name, portfolio_df in portfolios.items():

    safe_name = name.replace(" ", "_").replace(".", "")
    save_path = os.path.join(summary_dir, f"{safe_name}_cc_summary.html")

    plot_summary(portfolio_df, spy_returns, name, mapping, copycat_objects[name].snapshots, save_path=summary_dir)

# New Section

In [ ]:
def get_last_available_value(series, date):
    """
    Returns the last available value in a Series
    at or before the given date.
    """
    eligible = series.loc[:date]
    if eligible.empty:
        return np.nan
    return eligible.iloc[-1]


snapshot_dates_comp = pd.to_datetime(SNAPSHOT_DATES)

# Prepare SPY series
spy_df = spy_returns.copy()
spy_df['Date'] = pd.to_datetime(spy_df['Date'])
spy_series = spy_df.set_index('Date')['cumulative_return_pct']

rows = {}

for politician, df in portfolios.items():
    df = df.copy()
    df['Date'] = pd.to_datetime(df['Date'])
    portfolio_series = df.set_index('Date')['cumulative_return_pct']

    row = {}

    for date in snapshot_dates_comp:
        portfolio_val = get_last_available_value(portfolio_series, date)
        spy_val = get_last_available_value(spy_series, date)

        if pd.notna(portfolio_val) and pd.notna(spy_val):
            row[date.strftime('%Y-%m-%d')] = portfolio_val - spy_val
        else:
            row[date.strftime('%Y-%m-%d')] = np.nan

    rows[politician] = row

comparison_table = pd.DataFrame.from_dict(rows, orient='index')
comparison_table

2019-01-03  2019-12-31  2020-12-31   2021-12-31  \
Josh Gottheimer                  0.0  157.524666  174.812910   132.015761   
Nancy Pelosi                     0.0  -34.292086   79.252611    25.990391   
Kevin Hern                       0.0   72.863306   68.366270    13.125596   
Mark Green                       0.0  -34.292086   67.443545    61.455379   
Bradley S. Schneider             0.0  -34.292086  -58.910028  -104.562874   
Virginia Foxx                    0.0  104.261154   48.651359    14.322813   
Kim Schrier                      0.0  -34.292086  -58.910028    19.275389   
Mikie Sherrill                   0.0   73.555595   90.493959    82.224275   
Daniel Meuser                    0.0  -34.292086  -58.910028    -3.915736   
Susie Lee                        0.0   81.315170   69.395920    38.359941   
John W. Rose                     0.0  -34.292086  -58.910028  -104.562874   
Brian Mast                       0.0  103.556309  -58.910028  1364.130826   
Carol Devine Miller              0.0  -34.292086   46.373051    27.324555   
Michael C. Burgess               0.0  -34.292086  -58.910028    -4.562874   
Pete Sessions                    0.0  -34.292086  -58.910028   102.717748   
Lois Frankel                     0.0  104.149732   66.037113    43.373434   
Earl Blumenauer                  0.0  128.715197   97.099115    94.014633   
Michael Garcia                   0.0  -34.292086  283.988179   160.449848   
Donald Sternoff Beyer Jr         0.0   66.722314  207.605745   265.680376   
Debbie Dingell                   0.0  130.564141  105.775345   184.720861   

                            2022-12-31   2023-12-31    2024-12-31  \
Josh Gottheimer             103.949839   126.664348 -1.637559e+02   
Nancy Pelosi                  9.249698   -19.700488 -4.148932e+01   
Kevin Hern                   36.505355     8.438036 -2.736850e+01   
Mark Green                  137.736873   312.810413  1.146575e+04   
Bradley S. Schneider        -67.382838  -111.196609 -1.637559e+02   
Virginia Foxx               129.117443    83.895000  4.081743e+01   
Kim Schrier                 -67.382838  -111.196609 -1.637559e+02   
Mikie Sherrill               78.354979    74.644835  6.458164e+01   
Daniel Meuser                 5.892793   -10.800648 -4.368749e+01   
Susie Lee                    47.768433    34.681748  3.209211e+00   
John W. Rose                -67.382838  -111.196609 -1.637559e+02   
Brian Mast                  -67.382838  -111.196609 -1.637559e+02   
Carol Devine Miller          48.898896     6.918803 -3.407100e+01   
Michael C. Burgess           50.315392    -3.117860 -5.821471e+01   
Pete Sessions                74.748676   139.640812  3.436511e+02   
Lois Frankel                 71.362661   107.897726  9.111413e+01   
Earl Blumenauer              48.822386    25.459183 -2.055591e+01   
Michael Garcia               18.874831  -111.196609 -1.637559e+02   
Donald Sternoff Beyer Jr  70126.321183  2333.213654  4.425071e+07   
Debbie Dingell              152.895762    69.540761  6.600570e+01   

                            2025-01-02  
Josh Gottheimer          -1.637559e+02  
Nancy Pelosi             -3.976319e+01  
Kevin Hern               -2.750984e+01  
Mark Green                1.164341e+04  
Bradley S. Schneider     -1.637559e+02  
Virginia Foxx             4.353213e+01  
Kim Schrier              -1.637559e+02  
Mikie Sherrill            6.439282e+01  
Daniel Meuser            -4.431878e+01  
Susie Lee                 3.429735e+00  
John W. Rose             -1.637559e+02  
Brian Mast               -1.637559e+02  
Carol Devine Miller      -3.421807e+01  
Michael C. Burgess       -5.884776e+01  
Pete Sessions             3.454492e+02  
Lois Frankel              9.043958e+01  
Earl Blumenauer          -2.137780e+01  
Michael Garcia           -1.637559e+02  
Donald Sternoff Beyer Jr  4.425071e+07  
Debbie Dingell            6.560455e+01

In [ ]:
comparison_table.describe()

2019-01-03  2019-12-31  2020-12-31   2021-12-31    2022-12-31  \
count        20.0   20.000000   20.000000    20.000000     20.000000   
mean          0.0   34.015336   49.646246   120.578873   3543.564192   
std           0.0   73.007643   99.289637   305.674565  15672.100895   
min           0.0  -34.292086  -58.910028  -104.562874    -67.382838   
25%           0.0  -34.292086  -58.910028    14.023509      8.410471   
50%           0.0   16.215114   66.740329    40.866687     48.860641   
75%           0.0  103.704665   92.145248   110.042251     84.753694   
max           0.0  157.524666  283.988179  1364.130826  70126.321183   

        2023-12-31    2024-12-31    2025-01-02  
count    20.000000  2.000000e+01  2.000000e+01  
mean    136.710164  2.213079e+06  2.213088e+06  
std     527.999321  9.894631e+06  9.894629e+06  
min    -111.196609 -1.637559e+02 -1.637559e+02  
25%     -42.574518 -1.637559e+02 -1.637559e+02  
50%      16.948609 -3.071975e+01 -3.086395e+01  
75%      89.895682  6.493765e+01  6.469575e+01  
max    2333.213654  4.425071e+07  4.425071e+07

In [ ]:
    # # Individual return plots
    # individual_dir = os.path.join(OUTPUT_DIR, 'individual_returns')
    # os.makedirs(individual_dir, exist_ok=True)

    # for name, portfolio_df in portfolios.items():
    #     safe_name = name.replace(" ", "_").replace(".", "")
    #     save_path = os.path.join(individual_dir, f"{safe_name}_returns.html")
    #     plot_individual_returns(portfolio_df, spy_returns, name, save_path)

    # # Combined comparison plot
    # combined_path = os.path.join(OUTPUT_DIR, 'all_portfolios_comparison.html')
    # plot_all_portfolios(portfolios, spy_returns, save_path=combined_path)

    # # Pie chart snapshots
    # print("  Generating position pie charts...")
    # pie_dir = os.path.join(OUTPUT_DIR, 'position_snapshots')
    # os.makedirs(pie_dir, exist_ok=True)

    # for name, copycat in copycat_objects.items():
    #     plot_all_snapshots_for_legislator(copycat, name, pie_dir)

In [ ]:
# def plot_individual_returns(portfolio_df, spy_df, legislator_name, save_path=None):
#     """Plot individual portfolio returns vs SPY."""
#     fig = go.Figure()

#     # Portfolio returns
#     fig.add_trace(go.Scatter(
#         x=portfolio_df['Date'],
#         y=portfolio_df['cumulative_return_pct'],
#         mode='lines',
#         name=legislator_name,
#         line=dict(width=2)
#     ))

#     # SPY returns
#     fig.add_trace(go.Scatter(
#         x=spy_df['Date'],
#         y=spy_df['cumulative_return_pct'],
#         mode='lines',
#         name='SPY',
#         line=dict(width=2, dash='dash', color='gray')
#     ))

#     fig.update_layout(
#         title=f'{legislator_name} Portfolio vs SPY',
#         xaxis_title='Date',
#         yaxis_title='Cumulative Return (%)',
#         template='plotly_white',
#         legend=dict(x=0.02, y=0.98),
#         hovermode='x unified'
#     )

#     if save_path:
#         fig.write_html(save_path)

#     return fig

In [ ]:
# def plot_all_portfolios(portfolios_dict, spy_df, save_path=None):
#     """Plot all portfolios comparison."""
#     fig = go.Figure()

#     colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd',
#               '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf',
#               '#aec7e8', '#ffbb78', '#98df8a', '#ff9896', '#c5b0d5',
#               '#c49c94', '#f7b6d2', '#c7c7c7', '#dbdb8d', '#9edae5']

#     for i, (name, df) in enumerate(portfolios_dict.items()):
#         fig.add_trace(go.Scatter(
#             x=df['Date'],
#             y=df['cumulative_return_pct'],
#             mode='lines',
#             name=name,
#             line=dict(width=1.5, color=colors[i % len(colors)])
#         ))

#     # SPY
#     fig.add_trace(go.Scatter(
#         x=spy_df['Date'],
#         y=spy_df['cumulative_return_pct'],
#         mode='lines',
#         name='SPY',
#         line=dict(width=3, color='black', dash='dash')
#     ))

#     fig.update_layout(
#         title='All Copy-Cat Portfolios vs SPY',
#         xaxis_title='Date',
#         yaxis_title='Cumulative Return (%)',
#         template='plotly_white',
#         legend=dict(x=1.02, y=1, font=dict(size=9)),
#         hovermode='x unified',
#         height=700,
#         width=1200
#     )

#     if save_path:
#         fig.write_html(save_path)

#     return fig

In [ ]:
# def plot_position_pie(holdings_dict, date_str, legislator_name, save_path=None):
#     """Plot pie chart of portfolio positions."""
#     if not holdings_dict:
#         return None

#     # Sort by value and take top 10
#     sorted_holdings = sorted(holdings_dict.items(), key=lambda x: x[1], reverse=True)

#     if len(sorted_holdings) > 10:
#         top_10 = sorted_holdings[:10]
#         other_value = sum(v for _, v in sorted_holdings[10:])
#         top_10.append(('Other', other_value))
#         sorted_holdings = top_10

#     labels = [h[0] for h in sorted_holdings]
#     values = [h[1] for h in sorted_holdings]

#     fig = go.Figure(data=[go.Pie(
#         labels=labels,
#         values=values,
#         textinfo='label+percent',
#         textposition='outside'
#     )])

#     fig.update_layout(
#         title=f'{legislator_name} Portfolio - {date_str}',
#         template='plotly_white'
#     )

#     if save_path:
#         fig.write_html(save_path)

#     return fig



In [ ]:
# def plot_all_snapshots_for_legislator(copycat_portfolio, legislator_name, save_dir):
#     """Generate all pie chart snapshots for a legislator."""
#     for date_str, holdings in copycat_portfolio.snapshots.items():
#         if holdings:
#             safe_name = legislator_name.replace(" ", "_").replace(".", "")
#             filename = f"{safe_name}_position_{date_str.replace('-', '')}.html"
#             save_path = os.path.join(save_dir, filename)
#             plot_position_pie(holdings, date_str, legislator_name, save_path)



In [ ]:
    # # Individual return plots
    # individual_dir = os.path.join(OUTPUT_DIR, 'individual_returns')
    # os.makedirs(individual_dir, exist_ok=True)

    # for name, portfolio_df in portfolios.items():
    #     safe_name = name.replace(" ", "_").replace(".", "")
    #     save_path = os.path.join(individual_dir, f"{safe_name}_returns.html")
    #     plot_individual_returns(portfolio_df, spy_returns, name, save_path)

    # # Combined comparison plot
    # combined_path = os.path.join(OUTPUT_DIR, 'all_portfolios_comparison.html')
    # plot_all_portfolios(portfolios, spy_returns, save_path=combined_path)

    # # Pie chart snapshots
    # print("  Generating position pie charts...")
    # pie_dir = os.path.join(OUTPUT_DIR, 'position_snapshots')
    # os.makedirs(pie_dir, exist_ok=True)

    # for name, copycat in copycat_objects.items():
    #     plot_all_snapshots_for_legislator(copycat, name, pie_dir)

# Portfolio optimization

In [ ]:
def get_risk_free_rate():
    """Fetch 3-month US Treasury Bill rate from FRED via yfinance."""
    try:
        # ^IRX is the 13-week Treasury Bill rate
        tbill = yf.download('^IRX', period='5d', progress=False)
        if not tbill.empty:
            rate = tbill['Close'].iloc[-1].item() / 100  # Convert to decimal
            return rate
    except Exception as e:
        print(f"Could not fetch T-bill rate: {e}")
    # Default fallback
    return 0.045  # 4.5% as fallback


def get_top_n_stocks_at_date(congressmen_list, date, n=20, prices_df=None):
    """
    Get top N stocks by NET dollar exposure across all congressmen.
    Uses get_position() which calculates: buys(+) - sells(-).
    Only returns stocks with positive net exposure AND valid price data.

    Args:
        congressmen_list: List of Congressman_df objects
        date: Date to evaluate positions
        n: Number of top stocks to return
        prices_df: DataFrame of prices - stocks not in this df are excluded

    Returns:
        List of (ticker, net_amount) tuples sorted by exposure
    """
    all_holdings = {}
    as_of = pd.to_datetime(date)

    for congressman in congressmen_list:
        # Use get_position which already calculates net positions
        positions = congressman.get_position(as_of)

        for ticker, net_amount in positions.items():
            if net_amount > 0:  # Only positive net positions
                # Filter: only include if ticker exists in prices_df
                if prices_df is not None:
                    if ticker not in prices_df.columns:
                        continue
                    # Also check if there's actually data for this ticker
                    if prices_df[ticker].dropna().empty:
                        continue

                all_holdings[ticker] = all_holdings.get(ticker, 0) + net_amount

    # Sort by net exposure and return top N
    sorted_stocks = sorted(all_holdings.items(), key=lambda x: x[1], reverse=True)
    return sorted_stocks[:n]


def get_rebalance_dates(start_date, end_date, freq='quarterly'):
    """
    Generate rebalancing dates based on frequency.
    Adjusts non-business days to nearest earlier business day.

    Args:
        start_date, end_date: Date range
        freq: 'weekly', 'bi-weekly', 'monthly', 'quarterly', 'annually'

    Returns:
        List of rebalance dates (all business days)
    """
    start_dt = pd.to_datetime(start_date)
    end_dt = pd.to_datetime(end_date)

    freq_map = {
        'weekly': 'W-FRI',
        'bi-weekly': '2W-FRI',
        'monthly': 'ME',
        'quarterly': 'QE',
        'annually': 'YE'
    }

    pandas_freq = freq_map.get(freq, 'QE')
    dates = pd.date_range(start=start_dt, end=end_dt, freq=pandas_freq)

    # Ensure start date is included as first rebalance
    if len(dates) == 0 or dates[0] > start_dt:
        dates = pd.DatetimeIndex([start_dt]).append(dates)

    # Adjust to nearest earlier business day if not a business day
    adjusted_dates = []
    for d in dates:
        # If weekend, roll back to Friday
        if d.weekday() == 5:  # Saturday
            d = d - timedelta(days=1)
        elif d.weekday() == 6:  # Sunday
            d = d - timedelta(days=2)
        adjusted_dates.append(d)

    return adjusted_dates



In [ ]:
class CustomPortfolio:
    """
    Builds optimized portfolio from top N congressional holdings.

    Weighting schemes:
    - equal_share_weight: Equal number of shares per stock
    - equal_value: Equal dollar value per stock (1/N of capital each)
    - mean_variance: Optimize using historical returns/covariance

    Return Calculation:
    - daily_return = stock_value.pct_change()
    - On rebalance days, invest exactly prev_stock_value to ensure continuity
    - cumulative_return = (1 + daily_return).cumprod() - 1
    """

    def __init__(self, congressmen_list, prices_df,
                 rebalance_freq='quarterly', n_stocks=20,
                 lookback_months=12, weighting='equal_value'):
        self.congressmen_list = congressmen_list
        self.prices_df = prices_df
        self.rebalance_freq = rebalance_freq
        self.n_stocks = n_stocks
        self.lookback_months = lookback_months
        self.weighting = weighting

        self.holdings = {}  # {ticker: shares}
        self.holdings_history = {}  # {date: holdings_dict}
        self.history = None
        self.rebalance_log = []

    def simulate(self, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE, debug=False):
        """Run day-by-day simulation with periodic rebalancing."""
        start_dt = pd.to_datetime(start_date)
        end_dt = pd.to_datetime(end_date)

        # Reset state
        self.holdings = {}
        self.holdings_history = {}
        self.rebalance_log = []

        # Get rebalance dates
        rebalance_dates = get_rebalance_dates(start_date, end_date, self.rebalance_freq)
        rebalance_set = set(d.date() for d in rebalance_dates)

        if debug:
            print(f"Rebalance dates: {len(rebalance_dates)}")
            print(f"First 5: {[d.strftime('%Y-%m-%d') for d in rebalance_dates[:5]]}")

        # Generate daily values
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')

        records = []
        prev_stock_value = None

        for date in date_range:
            date_key = date.date()

            # Rebalance on rebalance dates
            if date_key in rebalance_set:
                # Amount to invest = previous day's stock value (for continuity)
                # On first rebalance, use INITIAL_CAPITAL
                amount_to_invest = prev_stock_value if prev_stock_value is not None else INITIAL_CAPITAL

                if debug:
                    print(f"REBALANCE {date.strftime('%Y-%m-%d')}: investing ${amount_to_invest:,.0f}")

                self._rebalance(date, amount_to_invest)

            # Calculate stock holdings value
            stock_value = self._calculate_stock_value(date)

            # Store holdings snapshot for this date
            self.holdings_history[date] = dict(self.holdings)

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'n_holdings': len(self.holdings)
            })

            prev_stock_value = stock_value

        # Create DataFrame and calculate returns
        df = pd.DataFrame(records)

        if not df.empty:
            # Daily return = percentage change of stock_value
            df['daily_return'] = df['stock_value'].pct_change().fillna(0)

            # Cumulative return = cumprod of (1 + daily_return) - 1
            df['cumulative_return'] = (1 + df['daily_return']).cumprod() - 1
            df['cumulative_return_pct'] = df['cumulative_return'] * 100

            # Log returns
            df['log_return'] = np.log(1 + df['daily_return']).replace([np.inf, -np.inf], 0).fillna(0)
            df['cumulative_log_return'] = df['log_return'].cumsum()

        self.history = df
        return df

    def _rebalance(self, date, amount_to_invest):
        """Rebalance portfolio: sell all, buy new top N stocks.

        Key: invest exactly amount_to_invest (= prev day's stock value)
        to ensure stock_value continuity across rebalance.
        """
        # Get top N stocks
        top_stocks = get_top_n_stocks_at_date(self.congressmen_list, date, self.n_stocks,  prices_df=self.prices_df)

        if not top_stocks:
            return

        tickers = [t[0] for t in top_stocks]

        # Clear holdings
        self.holdings = {}

        # Get weights
        weights = self._get_weights(tickers, date)

        # Buy new positions
        for ticker, weight in zip(tickers, weights):
            if weight <= 0:
                continue

            price = get_price_on_date(self.prices_df, ticker, date)
            if price is None or price <= 0:
                continue

            dollars = amount_to_invest * weight
            shares = dollars / price
            self.holdings[ticker] = shares

        self.rebalance_log.append({
            'date': date,
            'amount_invested': amount_to_invest,
            'n_stocks': len(self.holdings),
            'tickers': list(self.holdings.keys())
        })

    def _get_weights(self, tickers, date):
        """Calculate portfolio weights based on weighting scheme.
        Only includes tickers that have valid prices in prices_df.
        """
        # First, filter to tickers that have valid prices
        valid_tickers = []
        valid_prices = []

        for t in tickers:
            p = get_price_on_date(self.prices_df, t, date)
            if p is not None and p > 0:
                valid_tickers.append(t)
                valid_prices.append(p)

        n = len(valid_tickers)
        if n == 0:
            return [0] * len(tickers)  # No valid tickers

        if self.weighting == 'equal_share_weight':
            # Equal number of shares - weight proportional to 1/price
            total_price = sum(valid_prices)
            valid_weights = [p / total_price for p in valid_prices]

        elif self.weighting == 'equal_value':
            # Equal dollar value per stock
            valid_weights = [1 / n] * n

        elif self.weighting == 'mean_variance':
            return self._calculate_mean_variance_weights(tickers, date)

        else:
            valid_weights = [1 / n] * n

        # Map back to original ticker list (0 weight for missing tickers)
        weight_map = dict(zip(valid_tickers, valid_weights))
        return [weight_map.get(t, 0) for t in tickers]

    def _calculate_mean_variance_weights(self, tickers, date):
        """Calculate mean-variance optimal weights (minimum variance)."""
        n = len(tickers)

        # Get historical returns
        end_date = pd.to_datetime(date)
        start_date = end_date - timedelta(days=self.lookback_months * 30)

        returns_data = []
        valid_tickers = []

        for ticker in tickers:
            if ticker not in self.prices_df.columns:
                continue

            prices = self.prices_df[ticker].loc[start_date:end_date].dropna()
            if len(prices) < 20:
                continue

            returns = prices.pct_change().dropna()
            if len(returns) > 0:
                returns_data.append(returns)
                valid_tickers.append(ticker)

        if len(valid_tickers) < 2:
            return [1 / n] * n

        # Align returns
        returns_df = pd.DataFrame({t: r for t, r in zip(valid_tickers, returns_data)})
        returns_df = returns_df.dropna()

        if len(returns_df) < 2:
            return [1 / n] * n

        # Covariance matrix
        cov_matrix = returns_df.cov().values
        n_valid = len(valid_tickers)

        # Minimize variance
        def portfolio_variance(w):
            return w @ cov_matrix @ w

        constraints = {'type': 'eq', 'fun': lambda w: np.sum(w) - 1}
        bounds = [(0, 0.25) for _ in range(n_valid)]
        x0 = np.array([1 / n_valid] * n_valid)

        try:
            result = minimize(portfolio_variance, x0, method='SLSQP',
                            bounds=bounds, constraints=constraints)
            optimized = result.x if result.success else x0
        except:
            optimized = x0

        # Map back to original tickers
        ticker_weights = dict(zip(valid_tickers, optimized))
        weights = [ticker_weights.get(t, 0) for t in tickers]

        # Normalize
        total = sum(weights)
        if total > 0:
            weights = [w / total for w in weights]
        else:
            weights = [1 / n] * n

        return weights

    def _calculate_stock_value(self, date):
        """Calculate total value of stock holdings."""
        total = 0
        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                total += shares * price
        return total

    def get_portfolio_composition(self, date=None):
        """
        Get detailed portfolio composition at a specific date.
        Uses holdings_history from simulation if date is provided.

        Returns:
            DataFrame with: Asset, Type, Shares, Price, Value, Weight (%)
        """
        if date:
            as_of = pd.to_datetime(date)
            # Look up holdings from history for this date
            # Find the closest date in holdings_history that is <= as_of
            available_dates = sorted(self.holdings_history.keys())
            holdings_to_use = {}
            for d in available_dates:
                if d <= as_of:
                    holdings_to_use = self.holdings_history[d]
                else:
                    break
            if not holdings_to_use and available_dates:
                # If date is before first rebalance, use first available
                holdings_to_use = self.holdings_history[available_dates[0]]
        else:
            as_of = None
            holdings_to_use = self.holdings  # Use current holdings

        records = []
        total_stock_value = 0
        missing_tickers = []

        # Add stock holdings
        for ticker, shares in holdings_to_use.items():
            if as_of:
                price = get_price_on_date(self.prices_df, ticker, as_of)
            else:
                if ticker in self.prices_df.columns:
                    prices = self.prices_df[ticker].dropna()
                    price = prices.iloc[-1] if not prices.empty else None
                else:
                    price = None

            if price is not None and price > 0:
                value = shares * price
                total_stock_value += value
                records.append({
                    'Asset': ticker, 'Type': 'Stock',
                    'Shares': shares, 'Price': price, 'Value': value
                })
            else:
                missing_tickers.append(ticker)
                records.append({
                    'Asset': ticker, 'Type': 'Stock',
                    'Shares': shares, 'Price': None, 'Value': 0
                })

        df = pd.DataFrame(records)

        # Calculate weights based on total stock value
        if not df.empty and total_stock_value > 0:
            df['Weight (%)'] = (df['Value'] / total_stock_value * 100).round(2)
        elif not df.empty:
            df['Weight (%)'] = 0

        if not df.empty:
            df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Print summary
        date_str = as_of.strftime('%Y-%m-%d') if as_of else 'Current'
        print(f"\n{'='*70}")
        print(f"Portfolio Composition - {date_str}")
        print(f"Weighting: {self.weighting}, Rebalance: {self.rebalance_freq}")
        print(f"{'='*70}")
        print(f"Total Value:         ${total_stock_value:,.2f}")
        print(f"Number of Positions: {len(holdings_to_use)}")
        if missing_tickers:
            print(f"Missing Prices:      {len(missing_tickers)} - {missing_tickers[:5]}")
        print(f"{'='*70}\n")

        return df


## Equal Share Weighted portfolio

In [ ]:
equal_share_weight = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight')
equal_share_weight.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20      0.000000           0.000000   
1    2019-01-04  103336.630152          20      0.033366           0.033366   
2    2019-01-07  104713.287877          20      0.013322           0.047133   
3    2019-01-08  106011.347592          20      0.012396           0.060113   
4    2019-01-09  106130.266322          20      0.001122           0.061303   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  228893.339684          20     -0.010647           1.288933   
1562 2024-12-30  226166.261374          20     -0.011914           1.261663   
1563 2024-12-31  226166.261374          20      0.000000           1.261663   
1564 2025-01-01  226166.261374          20      0.000000           1.261663   
1565 2025-01-02  225588.307183          20     -0.002555           1.255883   

      cumulative_return_pct  log_return  cumulative_log_return  
0                  0.000000    0.000000               0.000000  
1                  3.336630    0.032822               0.032822  
2                  4.713288    0.013234               0.046056  
3                  6.011348    0.012320               0.058376  
4                  6.130266    0.001121               0.059497  
...                     ...         ...                    ...  
1561             128.893340   -0.010704               0.828086  
1562             126.166261   -0.011986               0.816100  
1563             126.166261    0.000000               0.816100  
1564             126.166261    0.000000               0.816100  
1565             125.588307   -0.002559               0.813542  

[1566 rows x 8 columns]

## Equal market cap portfolio

In [ ]:
equal_value = CustomPortfolio(congressmen, prices_df, weighting='equal_value')
equal_value.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20  0.000000e+00           0.000000   
1    2019-01-04  103442.419046          20  3.442419e-02           0.034424   
2    2019-01-07  105294.570042          20  1.790514e-02           0.052946   
3    2019-01-08  106726.973301          20  1.360377e-02           0.067270   
4    2019-01-09  107159.215172          20  4.049978e-03           0.071592   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  276094.651862          20 -9.270345e-03           1.760947   
1562 2024-12-30  273066.846312          20 -1.096655e-02           1.730668   
1563 2024-12-31  273066.846312          20  4.440892e-16           1.730668   
1564 2025-01-01  273066.846312          20  0.000000e+00           1.730668   
1565 2025-01-02  272961.018026          20 -3.875545e-04           1.729610   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  3.442419  3.384493e-02               0.033845  
2                  5.294570  1.774673e-02               0.051592  
3                  6.726973  1.351207e-02               0.065104  
4                  7.159215  4.041799e-03               0.069146  
...                     ...           ...                    ...  
1561             176.094652 -9.313582e-03               1.015574  
1562             173.066846 -1.102712e-02               1.004546  
1563             173.066846  4.440892e-16               1.004546  
1564             173.066846  0.000000e+00               1.004546  
1565             172.961018 -3.876296e-04               1.004159  

[1566 rows x 8 columns]

## Mean-Variance portfolio

In [ ]:
mean_var = CustomPortfolio(congressmen, prices_df, weighting='mean_variance')
mean_var.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          18  0.000000e+00           0.000000   
1    2019-01-04  102395.404583          18  2.395405e-02           0.023954   
2    2019-01-07  102882.124253          18  4.753335e-03           0.028821   
3    2019-01-08  103937.426553          18  1.025739e-02           0.039374   
4    2019-01-09  103408.169333          18 -5.092075e-03           0.034082   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  230961.424987          20 -9.270345e-03           1.309614   
1562 2024-12-30  228428.575185          20 -1.096655e-02           1.284286   
1563 2024-12-31  228428.575185          20 -3.330669e-16           1.284286   
1564 2025-01-01  228428.575185          20  0.000000e+00           1.284286   
1565 2025-01-02  228340.046662          20 -3.875545e-04           1.283400   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  2.395405  2.367165e-02               0.023672  
2                  2.882124  4.742074e-03               0.028414  
3                  3.937427  1.020514e-02               0.038619  
4                  3.408169 -5.105084e-03               0.033514  
...                     ...           ...                    ...  
1561             130.961425 -9.313582e-03               0.837081  
1562             128.428575 -1.102712e-02               0.826053  
1563             128.428575 -3.330669e-16               0.826053  
1564             128.428575  0.000000e+00               0.826053  
1565             128.340047 -3.876296e-04               0.825666  

[1566 rows x 8 columns]

## Metrics and Comparison

In [ ]:
def calculate_portfolio_metrics(history_df, risk_free_rate=None):
    """
    Calculate portfolio performance metrics.

    Returns:
        dict with: annualized_return, volatility, sharpe_ratio, max_drawdown
    """
    if risk_free_rate is None:
        risk_free_rate = get_risk_free_rate()

    if history_df is None or history_df.empty:
        return {
            'annualized_return': 0,
            'volatility': 0,
            'sharpe_ratio': 0,
            'max_drawdown': 0
        }

    # Daily returns from log returns
    if 'log_return' in history_df.columns:
        daily_returns = history_df['log_return'].dropna()
    else:
        daily_returns = history_df['portfolio_value'].pct_change().dropna()

    # Annualized metrics (252 trading days)
    mean_daily_return = daily_returns.mean()
    std_daily_return = daily_returns.std()

    annualized_return = mean_daily_return * 252
    volatility = std_daily_return * np.sqrt(252)

    # Sharpe ratio
    if volatility > 0:
        sharpe_ratio = (annualized_return - risk_free_rate) / volatility
    else:
        sharpe_ratio = 0

    # Maximum drawdown
    if 'portfolio_value' in history_df.columns:
        cumulative = history_df['portfolio_value']
    else:
        cumulative = (1 + daily_returns).cumprod()

    running_max = cumulative.expanding().max()
    drawdown = (cumulative - running_max) / running_max
    max_drawdown = drawdown.min()

    return {
        'annualized_return': annualized_return * 100,  # as percentage
        'volatility': volatility * 100,
        'sharpe_ratio': sharpe_ratio,
        'max_drawdown': max_drawdown * 100
    }


def compare_all_portfolios(copycat_portfolios, custom_portfolios, spy_df, risk_free_rate=None):
    """
    Compare all portfolios and return metrics DataFrame.

    Args:
        copycat_portfolios: dict of {name: CopycatPortfolio} or {name: history_df}
        custom_portfolios: dict of {name: CustomPortfolio} or {name: history_df}
        spy_df: SPY benchmark DataFrame

    Returns:
        DataFrame with comparison metrics
    """
    if risk_free_rate is None:
        risk_free_rate = get_risk_free_rate()

    results = []

    # Copycat portfolios
    for name, portfolio in copycat_portfolios.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio  # Assume it's already a DataFrame

        metrics = calculate_portfolio_metrics(history, risk_free_rate)
        metrics['name'] = name
        metrics['type'] = 'Copycat'
        results.append(metrics)

    # Custom portfolios
    for name, portfolio in custom_portfolios.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        metrics = calculate_portfolio_metrics(history, risk_free_rate)
        metrics['name'] = name
        metrics['type'] = 'Custom'
        results.append(metrics)

    # SPY benchmark
    spy_metrics = calculate_portfolio_metrics(spy_df, risk_free_rate)
    spy_metrics['name'] = 'SPY'
    spy_metrics['type'] = 'Benchmark'
    results.append(spy_metrics)

    # Create DataFrame
    df = pd.DataFrame(results)
    df = df[['name', 'type', 'annualized_return', 'volatility', 'sharpe_ratio', 'max_drawdown']]
    df.columns = ['Portfolio', 'Type', 'Ann. Return (%)', 'Volatility (%)', 'Sharpe Ratio', 'Max Drawdown (%)']

    # Sort by Sharpe ratio
    df = df.sort_values('Sharpe Ratio', ascending=False).reset_index(drop=True)

    return df


def print_comparison_table(comparison_df):
    """Print formatted comparison table."""
    print("\n" + "="*90)
    print("PORTFOLIO COMPARISON")
    print("="*90)
    print(f"\nRisk-Free Rate (3M T-Bill): {get_risk_free_rate()*100:.2f}%\n")
    print(comparison_df.to_string(index=False))
    print("\n" + "="*90)

In [ ]:
equal_share_weight_10 = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight', n_stocks=10)
equal_share_weight_10.simulate()
equal_value_10 = CustomPortfolio(congressmen, prices_df, weighting='equal_value', n_stocks=10)
equal_value_10.simulate()
mean_var_10 = CustomPortfolio(congressmen, prices_df, weighting='mean_variance', n_stocks=10)
mean_var_10.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000           8  0.000000e+00           0.000000   
1    2019-01-04  103289.850438           8  3.289850e-02           0.032899   
2    2019-01-07  105155.529571           8  1.806256e-02           0.051555   
3    2019-01-08  106907.617166           8  1.666187e-02           0.069076   
4    2019-01-09  107057.703231           8  1.403886e-03           0.070577   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  275705.754081          10 -1.102064e-02           1.757058   
1562 2024-12-30  272571.624295          10 -1.136766e-02           1.725716   
1563 2024-12-31  272571.624295          10  2.220446e-16           1.725716   
1564 2025-01-01  272571.624295          10  0.000000e+00           1.725716   
1565 2025-01-02  272882.034342          10  1.138820e-03           1.728820   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  3.289850  3.236893e-02               0.032369  
2                  5.155530  1.790137e-02               0.050270  
3                  6.907617  1.652458e-02               0.066795  
4                  7.057703  1.402901e-03               0.068198  
...                     ...           ...                    ...  
1561             175.705754 -1.108181e-02               1.014164  
1562             172.571624 -1.143277e-02               1.002731  
1563             172.571624  2.220446e-16               1.002731  
1564             172.571624  0.000000e+00               1.002731  
1565             172.882034  1.138172e-03               1.003869  

[1566 rows x 8 columns]

In [ ]:
equal_share_weight_5 = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight', n_stocks=5)
equal_share_weight_5.simulate()
equal_value_5 = CustomPortfolio(congressmen, prices_df, weighting='equal_value', n_stocks=5)
equal_value_5.simulate()
mean_var_5 = CustomPortfolio(congressmen, prices_df, weighting='mean_variance', n_stocks=5)
mean_var_5.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000           5      0.000000           0.000000   
1    2019-01-04  104306.432439           5      0.043064           0.043064   
2    2019-01-07  107401.099699           5      0.029669           0.074011   
3    2019-01-08  110013.061862           5      0.024320           0.100131   
4    2019-01-09  110394.300071           5      0.003465           0.103943   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  307785.292495           5     -0.014981           2.077853   
1562 2024-12-30  303713.346079           5     -0.013230           2.037133   
1563 2024-12-31  303713.346079           5      0.000000           2.037133   
1564 2025-01-01  303713.346079           5      0.000000           2.037133   
1565 2025-01-02  306811.427726           5      0.010201           2.068114   

      cumulative_return_pct  log_return  cumulative_log_return  
0                  0.000000    0.000000               0.000000  
1                  4.306432    0.042163               0.042163  
2                  7.401100    0.029237               0.071400  
3                 10.013062    0.024029               0.095429  
4                 10.394300    0.003459               0.098888  
...                     ...         ...                    ...  
1561             207.785292   -0.015094               1.124232  
1562             203.713346   -0.013318               1.110914  
1563             203.713346    0.000000               1.110914  
1564             203.713346    0.000000               1.110914  
1565             206.811428    0.010149               1.121063  

[1566 rows x 8 columns]

In [ ]:
custom_dict = {
    'Top20_EqualShare': equal_share_weight,
    'Top20_EqualValue': equal_value,
    'Top20_MeanVar': mean_var,
    'Top10_EqualShare': equal_share_weight_10,
    'Top10_EqualValue': equal_value_10,
    'Top10_MeanVar': mean_var_10,
    'Top5_EqualShare': equal_share_weight_5,
    'Top5_EqualValue': equal_value_5,
    'Top5_MeanVar': mean_var_5,
}

In [ ]:
comparison = compare_all_portfolios(copycat_objects, custom_dict, spy_returns)
print(comparison)


                   Portfolio       Type  Ann. Return (%)  Volatility (%)  \
0            Earl Blumenauer    Copycat        38.047423       27.588877   
1               Lois Frankel    Copycat        28.995408       30.558622   
2                  Susie Lee    Copycat        63.134558       74.405833   
3            Josh Gottheimer    Copycat        32.245266       36.481100   
4                 Kevin Hern    Copycat       149.633864      206.401021   
5              Pete Sessions    Copycat        20.260651       24.432009   
6             Mikie Sherrill    Copycat        88.451911      126.062523   
7           Top10_EqualValue     Custom        18.857489       22.909435   
8               Nancy Pelosi    Copycat        52.344227       73.993424   
9                        SPY  Benchmark        16.196369       19.889096   
10          Top20_EqualValue     Custom        16.158877       20.308768   
11       Carol Devine Miller    Copycat        41.182144       61.911022   
12          

In [ ]:
comparison.to_markdown(index=False)


'| Portfolio                | Type      |   Ann. Return (%) |   Volatility (%) |   Sharpe Ratio |   Max Drawdown (%) |\n|:-------------------------|:----------|------------------:|-----------------:|---------------:|-------------------:|\n| Earl Blumenauer          | Copycat   |          38.0474  |          27.5889 |      1.24885   |           -23.7559 |\n| Lois Frankel             | Copycat   |          28.9954  |          30.5586 |      0.831268  |           -31.2223 |\n| Susie Lee                | Copycat   |          63.1346  |          74.4058 |      0.800227  |           -51.2479 |\n| Josh Gottheimer          | Copycat   |          32.2453  |          36.4811 |      0.7854    |           -36.0014 |\n| Kevin Hern               | Copycat   |         149.634   |         206.401  |      0.707559  |          -131.269  |\n| Pete Sessions            | Copycat   |          20.2607  |          24.432  |      0.682206  |           -22.7246 |\n| Mikie Sherrill           | Copycat   |       

In [ ]:
comparison.to_csv(sep="\t", index=False)


'Portfolio\tType\tAnn. Return (%)\tVolatility (%)\tSharpe Ratio\tMax Drawdown (%)\nEarl Blumenauer\tCopycat\t38.04742297887028\t27.588876873306294\t1.2488519631278145\t-23.755932245526676\nLois Frankel\tCopycat\t28.995407935939106\t30.558621558149774\t0.8312681235457857\t-31.222280487944314\nSusie Lee\tCopycat\t63.13455844210035\t74.40583282599825\t0.800227028520615\t-51.2479212382617\nJosh Gottheimer\tCopycat\t32.2452663275254\t36.481100095644535\t0.7854002844556772\t-36.00138497220174\nKevin Hern\tCopycat\t149.63386353133285\t206.40102133622972\t0.7075588223872226\t-131.2693232642376\nPete Sessions\tCopycat\t20.26065096244249\t24.432009017952435\t0.6822055040600671\t-22.72455553415402\nMikie Sherrill\tCopycat\t88.4519108636431\t126.06252328075776\t0.6731493922226278\t-48.67494230186243\nTop10_EqualValue\tCustom\t18.85748898697824\t22.909435365406466\t0.6662970434826893\t-39.15068788251862\nNancy Pelosi\tCopycat\t52.34422671055383\t73.99342420037796\t0.6588589094536682\t-124.981060812

## Visualization

In [ ]:
def plot_custom_portfolios_comparison(custom_portfolios_dict, spy_df, save_path=None):
    """
    Plot custom portfolios vs SPY.
    Shows both cumulative return (%) and cumulative log return.
    """
    fig = make_subplots(
        rows=2, cols=1,
        subplot_titles=('Cumulative Return (%)', 'Cumulative Log Return'),
        vertical_spacing=0.12
    )

    color_list = px.colors.qualitative.T10
    portfolio_names = list(custom_portfolios_dict.keys())
    colors = {name: color_list[i % len(color_list)] for i, name in enumerate(portfolio_names)}

    # Top plot: Cumulative Returns
    for name, portfolio in custom_portfolios_dict.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        if history is None or history.empty:
            continue

        fig.add_trace(go.Scatter(
            x=history['Date'],
            y=history['cumulative_return_pct'],
            mode='lines',
            name=f'{name} (Return %)',
            line=dict(width=2, color=colors.get(name, '#333'))
        ), row=1, col=1)

    # SPY cumulative returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_return_pct'],
        mode='lines',
        name='SPY (Return %)',
        line=dict(width=2, dash='dash', color='gray')
    ), row=1, col=1)

    # Bottom plot: Log Returns
    for name, portfolio in custom_portfolios_dict.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        if history is None or history.empty or 'cumulative_log_return' not in history.columns:
            continue

        fig.add_trace(go.Scatter(
            x=history['Date'],
            y=history['cumulative_log_return'],
            mode='lines',
            name=f'{name} (Log)',
            line=dict(width=2, color=colors.get(name, '#333'))
        ), row=2, col=1)

    # SPY log returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_log_return'],
        mode='lines',
        name='SPY (Log)',
        line=dict(width=2, dash='dash', color='gray')
    ), row=2, col=1)

    # Layout
    fig.update_layout(
        title='Custom Portfolios vs SPY',
        template='plotly_white',
        height=700,
        legend=dict(
            x=1.02, y=1,  # move legend outside
            font=dict(size=10)
        ),
        hovermode='x unified'
    )
    fig.update_xaxes(title_text='Date', row=2, col=1)
    fig.update_yaxes(title_text='Cumulative Return (%)', row=1, col=1)
    fig.update_yaxes(title_text='Cumulative Log Return', row=2, col=1)


    filename = "CustomPortfolio.html"
    if save_path:
      fig.write_html(os.path.join(save_path, filename))

    return fig


In [ ]:
fig = plot_custom_portfolios_comparison(custom_dict, spy_returns, save_path=summary_dir)
fig.show()



In [ ]:
test = equal_share_weight.get_portfolio_composition('2023-01-15')
print(test)


Portfolio Composition - 2023-01-15
Weighting: equal_share_weight, Rebalance: quarterly
Total Value:         $165,466.30
Number of Positions: 20

   Asset   Type     Shares       Price         Value  Weight (%)
0   COST  Stock  53.197643  465.094879  24741.951562       14.95
1    UNH  Stock  53.197643  463.460266  24654.994001       14.90
2     HD  Stock  53.197643  306.887634  16325.698955        9.87
3    ROK  Stock  53.197643  270.806396  14406.262130        8.71
4    ACN  Stock  53.197643  270.588379  14394.664109        8.70
5   MSFT  Stock  53.197643  233.643814  12429.300322        7.51
6    TXN  Stock  53.197643  162.388962   8638.710093        5.22
7    JNJ  Stock  53.197643  158.310837   8421.763454        5.09
8    JPM  Stock  53.197643  133.200302   7085.942183        4.28
9   CRWD  Stock  53.197643   99.529999   5294.761390        3.20
10   TIP  Stock  53.197643   99.146301   5274.349587        3.19
11   EMR  Stock  53.197643   92.283279   4909.252997        2.97
12   RTX 

In [ ]:
test2 = equal_value.get_portfolio_composition('2023-01-15')
print(test2)


Portfolio Composition - 2023-01-15
Weighting: equal_value, Rebalance: quarterly
Total Value:         $191,052.82
Number of Positions: 20

   Asset   Type       Shares       Price         Value  Weight (%)
0    NGL  Stock  7512.290696    1.550000  11644.050220        6.09
1     AB  Stock   341.202895   30.252703  10322.309733        5.40
2   PYPL  Stock   127.925935   79.296692  10144.103460        5.31
3    ROK  Stock    37.171849  270.806396  10066.374382        5.27
4    TXN  Stock    60.647916  162.388962   9848.552140        5.15
5      T  Stock   591.463119   16.555775   9792.130130        5.13
6    JPM  Stock    73.313895  133.200302   9765.433017        5.11
7     ET  Stock  1001.691445    9.686116   9702.499751        5.08
8   COST  Stock    20.774997  465.094879   9662.344667        5.06
9    ACN  Stock    35.664419  270.588379   9650.377431        5.05
10    HD  Stock    31.058977  306.887634   9531.616028        4.99
11  DGRO  Stock   195.158355   47.890369   9346.205720   

In [ ]:
test3 = equal_value.get_portfolio_composition('2019-05-31')
print(test3)


Portfolio Composition - 2019-05-31
Weighting: equal_value, Rebalance: quarterly
Total Value:         $115,492.25
Number of Positions: 20

   Asset   Type      Shares       Price        Value  Weight (%)
0   TTWO  Stock   61.704575  108.150002  6673.349883        5.78
1    PGR  Stock   98.577685   65.051361  6412.612584        5.55
2   MSFT  Stock   52.544519  116.645180  6129.064826        5.31
3     SO  Stock  146.720877   41.562374  6098.067969        5.28
4   TDOC  Stock  104.731314   58.119999  6086.983874        5.27
5    CDW  Stock   65.504625   91.058044  5964.723062        5.16
6    BEP  Stock  454.970220   13.099223  5959.756431        5.16
7   DXCM  Stock  195.568799   30.325001  5930.623977        5.14
8    TTD  Stock  294.168269   19.881001  5848.359515        5.06
9   MIDD  Stock   44.782442  130.470001  5842.765298        5.06
10  AMZN  Stock   65.400096   88.753502  5804.487510        5.03
11     T  Stock  403.262434   14.380516  5799.121899        5.02
12   EPD  Stock 

In [ ]:
test4 = mean_var.get_portfolio_composition('2023-01-15')
print(test4)


Portfolio Composition - 2023-01-15
Weighting: mean_variance, Rebalance: quarterly
Total Value:         $159,821.39
Number of Positions: 20

   Asset   Type       Shares       Price        Value  Weight (%)
0    NGL  Stock  6284.255607    1.550000  9740.595891        6.09
1     AB  Stock   285.426415   30.252703  8634.920484        5.40
2   PYPL  Stock   107.013867   79.296692  8485.845613        5.31
3    ROK  Stock    31.095362  270.806396  8420.822917        5.27
4    TXN  Stock    50.733794  162.388962  8238.608104        5.15
5      T  Stock   494.776570   16.555775  8191.409407        5.13
6    JPM  Stock    61.329264  133.200302  8169.076474        5.11
7     ET  Stock   837.944821    9.686116  8116.430917        5.08
8   COST  Stock    17.378906  465.094879  8082.839990        5.06
9    ACN  Stock    29.834352  270.588379  8072.829039        5.05
10    HD  Stock    25.981762  306.887634  7973.481577        4.99
11  DGRO  Stock   163.255795   47.890369  7818.380316        4.89
1

In [ ]:
for k in custom_dict.keys():
  print(f"History for {k} Portfolio")
  print("\n")
  print(custom_dict[k].history)
  print("\n")
  print("-------------------------")

History for Top20_EqualShare Portfolio


           Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20      0.000000           0.000000   
1    2019-01-04  103336.630152          20      0.033366           0.033366   
2    2019-01-07  104713.287877          20      0.013322           0.047133   
3    2019-01-08  106011.347592          20      0.012396           0.060113   
4    2019-01-09  106130.266322          20      0.001122           0.061303   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  228893.339684          20     -0.010647           1.288933   
1562 2024-12-30  226166.261374          20     -0.011914           1.261663   
1563 2024-12-31  226166.261374          20      0.000000           1.261663   
1564 2025-01-01  226166.261374          20      0.000000           1.261663   
1565 2025-01-02  225588.307183          20     -0.002555           1.255883   

      cumu

In [ ]:
def get_value_asof(df, date, value_col):
    date = pd.to_datetime(date)
    df = df.sort_values("Date")

    sub = df[df["Date"] <= date]
    if sub.empty:
        return np.nan

    return sub.iloc[-1][value_col]

rows = {}

# ---- PORTFOLIOS ----
for name, portfolio in custom_dict.items():
    history = portfolio.history.copy()
    row = {}

    for date_str in SNAPSHOT_DATES:
        row[date_str] = get_value_asof(
            history,
            date_str,
            "cumulative_return_pct"
        )

    rows[name] = row


# ---- SPY BENCHMARK (SAME METRIC) ----
spy_row = {}

for date_str in SNAPSHOT_DATES:
    spy_row[date_str] = get_value_asof(
        spy_returns,
        date_str,
        "cumulative_return_pct"
    )

rows["SPY"] = spy_row


snapshot_return_table = pd.DataFrame(rows).T.round(2)
snapshot_return_table





2019-01-03  2019-12-31  2020-12-31  2021-12-31  2022-12-31  \
Top20_EqualShare         0.0       29.93       64.99      105.13       61.46   
Top20_EqualValue         0.0       34.21       63.39      112.67       81.80   
Top20_MeanVar            0.0       29.69       49.14       77.91       52.08   
Top10_EqualShare         0.0       23.18       66.79       99.23       53.56   
Top10_EqualValue         0.0       39.69       74.99      134.96       87.73   
Top10_MeanVar            0.0       30.63       56.27       98.62       58.70   
Top5_EqualShare          0.0       27.89       63.30       82.27        5.20   
Top5_EqualValue          0.0       47.87       81.53      145.18       84.09   
Top5_MeanVar             0.0       40.83       72.88      145.73       84.51   
SPY                      0.0       34.29       58.91      104.56       67.38   

                  2023-12-31  2024-12-31  2025-01-02  
Top20_EqualShare       94.10      126.17      125.59  
Top20_EqualValue      125.90      173.07      172.96  
Top20_MeanVar          88.97      128.43      128.34  
Top10_EqualShare       93.35      132.61      132.63  
Top10_EqualValue      161.68      222.43      222.80  
Top10_MeanVar         121.21      172.57      172.88  
Top5_EqualShare        48.22       97.69      100.10  
Top5_EqualValue       137.51      203.03      206.12  
Top5_MeanVar          138.05      203.71      206.81  
SPY                   111.20      163.76      163.76

In [ ]:
snapshot_return_table.describe()


2019-01-03  2019-12-31  2020-12-31  2021-12-31  2022-12-31  2023-12-31  \
count        10.0   10.000000   10.000000    10.00000    10.00000   10.000000   
mean          0.0   33.821000   65.219000   110.62600    63.65100  112.019000   
std           0.0    7.242714    9.476185    24.12469    24.62494   32.219106   
min           0.0   23.180000   49.140000    77.91000     5.20000   48.220000   
25%           0.0   29.750000   60.007500    98.77250    54.84500   93.537500   
50%           0.0   32.420000   64.190000   104.84500    64.42000  116.205000   
75%           0.0   38.340000   71.357500   129.38750    83.51750  134.607500   
max           0.0   47.870000   81.530000   145.73000    87.73000  161.680000   

       2024-12-31  2025-01-02  
count   10.000000   10.000000  
mean   162.347000  163.199000  
std     40.443946   40.867345  
min     97.690000  100.100000  
25%    129.475000  129.412500  
50%    168.165000  168.320000  
75%    195.540000  197.830000  
max    222.430000  222.800000